# Custom Suite, on Automatic Misogyny Identification

English data

## Imports

In [1]:
%load_ext autoreload
%autoreload 2

from nltk.corpus import wordnet as wn

import checklist
import spacy
import itertools
import pandas as pd

import checklist.editor
import checklist.text_generation
from checklist.test_types import MFT, INV, DIR
from checklist.expect import Expect
import numpy as np
import spacy
from checklist.test_suite import TestSuite
from checklist.perturb import Perturb

In [2]:
#conda install -c conda-forge jupyter_contrib_nbextensions

## Exploring and preparing the dataset about misogyny/gender 

### Resulting dataset (merged in the notebook 'Dataset_AMI')

The dataset contains:
* HatEval (only sexist post)
* AMI 2018 
* Waasem (only sexist post)
* Social Bias Frame (only post related to gender, sexual orientation, ecc.)
* Golbeck (only posts that cointain 'feminist') 

For now, we did not include Jigsaw gender-related post, cause they belongs to a slightly different genre

In [3]:
r=pd.read_csv('/Users/Marta/CheckList - FBK/Evaluation_Datasets/dataset_AMI.csv', index_col=None, header=0)
r=r[['text', 'misogynous']]
r

text  misogynous
0      Please tell me why the bitch next to me in the...         1.0
1      @emmasharp003 @Ldrake48Lee Bitch shut the fuck up         1.0
2          @abzdafab Dear cunt, please shut the fuck up.         1.0
3        RT @queenofdragonsb: Pls shut the fuck up bitch         1.0
4      RT @21bIvck: "when u gonna get your license" S...         1.0
...                                                  ...         ...
22229  https://twitter.com/marredblank/status/6690224...         0.0
22230  how feminists fail to understand the men's rig...         0.0
22231  people disagree with bullshit feminist tactics...         1.0
22232  it's amazing that feminists academics don't us...         0.0
22233  @ultradavid @samuraibeandog @lifefire940 i'm a...         0.0

[22234 rows x 2 columns]

## Using the comprehensive dataset and preprocessing the data

The confidence is = 1 because these are gold standards

In [4]:
labels = r['misogynous']
confs = [] 
for i in range(len(r)):  
    confs.append(1) 
tdata = r['text']

" spaCy is an open-source software library for advanced natural language processing: https://github.com/explosion/spaCy. spaCy comes with pretrained statistical models and word vectors, and currently supports tokenization for 60+ languages. It features state-of-the-art speed, convolutional neural network models for tagging, parsing and named entity recognition and easy deep learning integration. "

In [5]:
nlp = spacy.load('en_core_web_sm')

/Users/Marta/opt/anaconda3/lib/python3.6/site-packages/spacy/util.py:275: UserWarning: [W031] Model 'en_core_web_sm' (2.2.0) requires spaCy v2.2 and is incompatible with the current spaCy version (2.3.2). This may lead to unexpected results or runtime errors. To resolve this, download a newer compatible model or retrain your custom model with the current spaCy version. For more details and available updates, run: python -m spacy validate
  warnings.warn(warn_msg)


" When processing large volumes of text, the statistical models are usually more efficient if you let them work on batches of texts. spaCy’s nlp.pipe method takes an iterable of texts and yields processed Doc objects. The batching is done internally " https://spacy.io/usage/processing-pipelines#processing

In [6]:
sentences = tdata
parsed_data = list(nlp.pipe(sentences))

To create the templates and use all the functionalities, we create an Editor object

In [7]:
editor = checklist.editor.Editor()
editor.tg

Some weights of RobertaForMaskedLM were not initialized from the model checkpoint at roberta-base and are newly initialized: ['lm_head.decoder.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Creating a new object, TestSuite, where we'll add all the custom tests, inspired by the original notebooks plus new ones

In [8]:
suite = TestSuite()

# CheckList

" In order to guide test ideation, it's useful to think of CheckList as a matrix of Capabilities x Test Types.  
*Capabilities* refers to general-purpose linguistic capabilities, which manifest in one way or another in almost any NLP application.   
We suggest that anyone CheckListing a model go through *at least* the following capabilities, trying to create MFTs, INVs, and DIRs for each if possible.
1. **Vocabulary + POS:** important words or groups of words (by part-of-speech) for the task
2. **Taxonomy**: synonyms, antonyms, word categories, etc
3. **Robustness**: to typos, irrelevant additions, contractions, etc
4. **Named Entity Recognition (NER)**: person names, locations, numbers, etc
5. **Fairness**
6. **Temporal understanding**: understanding order of events and how they impact the task
7. **Negation**
8. **Coreference** 
9. **Semantic Role Labeling (SRL)**: understanding roles such as agent, object, passive/active, etc
10. **Logic**: symmetry, consistency, conjunctions, disjunctions, etc

Notice that we are framing this as very **top-down approach**: you start with a list of capabilities and try to think of what kinds of tests can be created, based on the three test types. 

**Bottom up approach**
In this approach, we look at specific examples (from the validation dataset or elsewhere) and try to generalize them into MFTs, INVs or DIRs, placing them into a specific capability.  "

## Exploring the linguistic data and tools available to build/expand lexicons and tests

Important words or word types for the task

### HurtLex

**HurtLex**

From the paper, section 4.2 Misogyny Identification on Social Media:
_They identified the Prostitution, Female and Male Sexual Apparatus and
Physical and Mental Diversity and Disability categories as the most informative for this task._ The task they are talking about is precisely AMI

In [9]:
hurtlex=pd.read_csv('/Users/Marta/CheckList - FBK/hurtlex/lexica/EN/1.2/hurtlex_EN.tsv', sep='\t', index_col=None, header=0)

In building the lexica, we filter out per POS = n, a, v, av 

Selecting the relevant categories: PR (words related to prostitution), ASM (male genitalia), ASF (female genitalia), DDF (physical disabilities and diversity), DDP (cognitive disabilities and diversity), OM (Homosexuality), QAS	(with potential negative connotations), CDS	(derogatory words)

In [10]:
hurtlex_AMI_pr=hurtlex[(hurtlex.category=='pr')]
hurtlex_AMI_asm=hurtlex[(hurtlex.category=='asm')]
hurtlex_AMI_asf=hurtlex[(hurtlex.category=='asf')]
hurtlex_AMI_dis=hurtlex[(hurtlex.category=='ddf')]
hurtlex_AMI_dis=hurtlex_AMI_dis.append(hurtlex[(hurtlex.category=='ddp')])
hurtlex_AMI_om=hurtlex[(hurtlex.category=='om')]
hurtlex_AMI_off=hurtlex[(hurtlex.category=='qas')]
hurtlex_AMI_off=hurtlex_AMI_off.append([(hurtlex.category=='cds')])

In [11]:
hurtlex_AMI_pr.head()

id pos category stereotype           lemma         level
26   EN940   n       pr         no         rentboy  conservative
54  EN2962   n       pr         no   courtisanerie     inclusive
64  EN1929   n       pr         no         beyotch  conservative
68   EN899   n       pr         no        sluttish  conservative
95  EN6018   n       pr         no  society figure     inclusive

In [12]:
hurtlex_AMI_asm.head()

id pos category stereotype     lemma         level
18    EN523   n      asm         no      putz  conservative
31   EN2677   n      asm         no  wankiest  conservative
70   EN1916   n      asm         no  half-wit     inclusive
97    EN861   n      asm         no      mark  conservative
152  EN2885   v      asm         no   barrack     inclusive

In [13]:
hurtlex_AMI_asf.head()

id pos category stereotype       lemma         level
51    EN337   n      asf         no    folderol  conservative
154  EN1925   n      asf         no     coo-yon  conservative
244  EN1913   n      asf         no  stupidhead  conservative
269  EN4197   n      asf         no        muff     inclusive
377   EN334   n      asf         no    trumpery  conservative

In [14]:
hurtlex_AMI_dis.head()

id pos category stereotype              lemma         level
479   EN7294   a      ddf        yes    dissatisfactory  conservative
791   EN4811   n      ddf        yes        disablement     inclusive
968   EN1784   a      ddf        yes              slimy  conservative
1107  EN4802   n      ddf        yes  differently-abled     inclusive
1803  EN4779   n      ddf        yes        handycapped     inclusive

In [15]:
hurtlex_AMI_om.head()

id pos category stereotype                        lemma         level
6    EN204   n       om         no                   buttfucker     inclusive
8    EN206   n       om         no                      assplay     inclusive
21  EN3241   n       om         no                 retrolateral     inclusive
35  EN2454   n       om         no             homophobic slurs  conservative
72  EN3234   n       om         no  anatomical term of location     inclusive

### Wordnet & SentiWordNet

**Wordnet & SentiWordNet**

' If syn is your synset, then syn.method() will deliver the value for all the different choices of method (e.g., hypernyms, part_meronyms()), and syn.attribute will give you the value of each attribute (name, pos, lemmas, definition, examples, offset). ' 

Finding neutral syn (using SentiWordNet)

In [16]:
editor.neutral('The girl see', 'girl')

["('daughter.n.01') Pos: 0.0 Neg: 0.0 Obj: 1.0",
 "('girl.n.05') Pos: 0.0 Neg: 0.0 Obj: 1.0",
 "('girlfriend.n.02') Pos: 0.0 Neg: 0.0 Obj: 1.0",
 "('girl.n.01') Pos: 0.0 Neg: 0.0 Obj: 1.0"]

In [17]:
editor.synonyms('The girl see', 'girl')

['miss', 'daughter', 'girlfriend']

Finding positive syn (using SentiWordNet)

In [18]:
editor.positive('The girl is happy', 'happy')

["('happy.a.01') Pos: 0.875 Neg: 0.0",
 "('felicitous.s.02') Pos: 0.75 Neg: 0.0",
 "('glad.s.02') Pos: 0.5 Neg: 0.0"]

In [19]:
editor.synonyms('The girl is happy', 'happy')

['glad']

In [20]:
editor.antonyms('The girl is', 'girl')

['boy', 'son']

Finding negative syn (using SentiWordNet)

In [21]:
editor.negative('The girl is mad', 'mad')

["('brainsick.s.01') Pos: 0.0 Neg: 0.5"]

In [22]:
editor.synonyms('The girl is mad', 'mad')

['sick', 'insane', 'crazy', 'excited', 'disturbed', 'sore', 'frantic']

Exploring related words with WordNet, comparing results for woman/girl vs man/boy

In [23]:
editor.hypernyms('The woman is', 'woman')

['cause',
 'object',
 'group',
 'class',
 'whole',
 'person',
 'individual',
 'entity',
 'soul',
 'unit',
 'organism',
 'people',
 'worker',
 'abstraction',
 'adult',
 'female',
 'being',
 'employee',
 'cleaner',
 'grouping']

In [24]:
editor.hypernyms('The man is', 'man')

['cause',
 'object',
 'work',
 'group',
 'whole',
 'beast',
 'person',
 'individual',
 'creature',
 'entity',
 'supply',
 'soul',
 'animal',
 'staff',
 'unit',
 'organism',
 'artifact',
 'equipment',
 'give',
 'worker',
 'human',
 'transfer',
 'abstraction',
 'adult',
 'assistant',
 'subsidiary',
 'help',
 'being',
 'servant',
 'male',
 'helper',
 'grouping',
 'brute',
 'supporter',
 'provide',
 'lover']

In [25]:
editor.hypernyms('The girl is', 'girl')

['issue',
 'cause',
 'object',
 'whole',
 'child',
 'person',
 'relation',
 'individual',
 'woman',
 'entity',
 'soul',
 'kid',
 'unit',
 'organism',
 'offspring',
 'adult',
 'female',
 'relative',
 'being',
 'lover']

In [26]:
editor.hypernyms('The boy is', 'boy')

['issue',
 'cause',
 'object',
 'whole',
 'man',
 'child',
 'person',
 'relation',
 'individual',
 'entity',
 'soul',
 'kid',
 'Black',
 'unit',
 'organism',
 'offspring',
 'Negro',
 'adult',
 'relative',
 'being',
 'male']

In [27]:
editor.hyponyms('The woman is', 'woman')

['beauty',
 'cat',
 'dish',
 'baby',
 'girl',
 'mother',
 'bird',
 'wife',
 'miss',
 'Wave',
 'broad',
 'baggage',
 'witch',
 'widow',
 'ex',
 'lady',
 'heroine',
 'peach',
 'whore',
 'sister',
 'doll',
 'girlfriend',
 'prostitute',
 'nurse',
 'mistress',
 'tease',
 'knockout',
 'Cinderella',
 'chick',
 'maiden',
 'gal',
 'babe',
 'deb',
 'skirt']

In [28]:
editor.hyponyms('The man is', 'man')

['world',
 'cat',
 'boy',
 'king',
 'guy',
 'gentleman',
 'crew',
 'horse',
 'queen',
 'bull',
 'bishop',
 'castle',
 'ex',
 'commander',
 'soldier',
 'humanity',
 'striker',
 'Don',
 'officer',
 'black',
 'Marine',
 'knight',
 'dude',
 'ranger',
 'veteran',
 'wolf',
 'Highlander',
 'aide',
 'vet',
 'PO',
 'volunteer',
 'fodder',
 'bachelor',
 'boyfriend',
 'KP',
 'gent',
 'recruit',
 'swell',
 'white',
 'tile',
 'tanker',
 'regular',
 'patriarch',
 'sod',
 'private',
 'SEAL']

In [29]:
editor.hyponyms('The girl is', 'girl')

['baby', 'bird', 'Scout', 'rover', 'sister', 'doll', 'chick', 'maiden', 'gal']

In [30]:
editor.hyponyms('The boy is', 'boy')

['Scout', 'rover', 'Junior']

The synsets and the examples bring out a somewhat sexist conception of women 

In [31]:
syns = wn.synsets('woman', 'n')
print(syns)

[Synset('woman.n.01'), Synset('woman.n.02'), Synset('charwoman.n.01'), Synset('womanhood.n.02')]


In [32]:
print(syns[0].definition())

an adult female person (as opposed to a man)


In [33]:
print(syns[1].definition())

a female person who plays a significant role (wife or mistress or girlfriend) in the life of a particular man


In [34]:
print(syns[0].examples())

['the woman kept house while the man hunted']


In [35]:
print(syns[1].examples())

['he was faithful to his woman']


In [36]:
print(syns[2].examples())

['the char will clean the carpet', 'I have a woman who comes in four hours a day while I write']


In [37]:
syns = wn.synsets('man', 'n')
print(syns)

[Synset('man.n.01'), Synset('serviceman.n.01'), Synset('man.n.03'), Synset('homo.n.02'), Synset('man.n.05'), Synset('man.n.06'), Synset('valet.n.01'), Synset('man.n.08'), Synset('man.n.09'), Synset('man.n.10'), Synset('world.n.08')]


In [38]:
print(syns[0].definition())

an adult person who is male (as opposed to a woman)


In [39]:
print(syns[1].definition())

someone who serves in the armed forces; a member of a military force


In [40]:
print(syns[0].examples())

['there were two women and six men on the bus']


In [41]:
print(syns[1].examples())

['two men stood sentry duty']


In [42]:
print(syns[2].examples())

['it was every man for himself']


In [43]:
w1 = wn.synset('woman.n.01')
w2 = wn.synset('man.n.01')
print(w1.wup_similarity(w2))

0.6666666666666666


In [44]:
w1.common_hypernyms(w2)

[Synset('object.n.01'),
 Synset('person.n.01'),
 Synset('physical_entity.n.01'),
 Synset('organism.n.01'),
 Synset('adult.n.01'),
 Synset('living_thing.n.01'),
 Synset('causal_agent.n.01'),
 Synset('entity.n.01'),
 Synset('whole.n.02')]

In [45]:
w1.lowest_common_hypernyms(w2)

[Synset('adult.n.01')]

### Expanding the lexicons

Exploring the lexicons.keys

In [46]:
print(list(editor.lexicons.keys()))

['male', 'female', 'first_name', 'first_pronoun', 'last_name', 'country', 'nationality', 'city', 'religion', 'religion_adj', 'sexual_adj', 'country_city', 'male_from', 'female_from', 'last_from']


_Names_

Some of the offensive terms taken from: 
* https://www.macmillandictionary.com/thesaurus-category/british/insulting-words-for-a-woman
* http://www.slate.com/blogs/lexicon_valley/2013/09/11/top_swear_words_most_popular_curse_words_on_facebook.html
* https://github.com/minerva-ml/open-solution-toxic-comments/blob/master/external_data/compiled_bad_words.txt
* https://github.com/RobertJGabriel/Google-profanity-words/blob/master/list.txt

In [47]:
# kind of neutral, taken by identity terms' file within AMI2020's data
women_noun = ['woman', 'sister', 'daughter', 'girl', 'wife', 'young lady', 'lady',
              'grandmother', 'mum', 'girlfriend', 'partner']#, 'bride', 'housewife', Mrs', 'Miss']

# We don't need plural in templates for now
#women_noun_plural = ['women', 'sisters', 'aunts', 'daughters', 'girls', 'mothers', 'wives', 'young ladies', 'ladies', 'brides', 
#              'grandmothers', 'mums', 'housewives', 'females', 'girlfriends', 'they']

# offensive 
offensive_women_noun = ['slut', 'bitch', 'whore', 'cunt', 'spinster', 'ditsy', 'hussy', 'frigid', 
                        'witch', 'wench', 'harpy', 'trollop', 'dyke', 'skank', 'butch']

# We don't need plural in templates for now
#offensive_women_noun_plural = ['sluts', 'bitches', 'whores', 'cunts']

offensive_homosexuals = []
for term in hurtlex_AMI_om[(hurtlex_AMI_om.pos=='n')&(hurtlex_AMI_om.level=='conservative')].lemma:
    offensive_homosexuals.append(term)

In [48]:
work_role = ['astronaut', 'academic', 'accountant', 'activist', 'administrator', 'advisor', 'agent', 'analyst','architect', 
             'assistant', 'attorney', 'artist' 'boxer', 'builder', 'businessman', 'cameraman', 'carpenter', 'clown', 
             'consultant', 'dentist', 'detective', 'developer', 'doctor', 'doorman', 'driver', 'electrician', 
             'economist', 'editor', 'educator', 'entrepreneur', 'executive',
             'engineer', 'farmer',  'fighter', 'fireman', 'footballer', 'foreman', 
             'historian', 'hitter', 'intern', 'interpreter', 'investigator', 'investor', 'gardener', 'housekeeper', 
             'journalist', 'librarian', 'lifeguard', 'magician', 'mechanic', 'nun', 'nurse', 'painter', 'paramedic', 
             'photographer', 'pilot', 'police', 'poet', 'postman', 'priest', 'professor', 'ranger', 'repairman', 'reporter', 
             'salesman', 'scientist', 'secretary', 'singer', 'soldier', 'student', 'surgeon', 'teacher', 'waiter', 'writer', 
             'attendant', 'officer', 'player', 'organizer', 'quarterback', 'shooter']

# These sterotyped lists are taken from the file male_occupations.txt and female_occupations.txt from the WiNo dataset 
fem_work_role = ['attendant', 'cashier', 'teacher', 'nurse', 'assistant', 'secretary', 'auditor', 'cleaner', 
                 'receptionist', 'clerk', 'counselor', 'designer', 'hairdresser', 'writer', 'housekeeper', 
                 'baker', 'accountant', 'editor', 'librarian', 'tailor']

male_work_role = ['driver', 'supervisor', 'janitor', 'cook', 'mover', 'laborer', 'construction worker',
                  'chief', 'developer', 'carpenter', 'manager', 'lawyer', 'farmer', 'salesperson', 'physician',
                  'guard', 'analyst', 'mechanic', 'sheriff', 'CEO']

For now we decide to not expand too much the lexicons, so we don't use Hurtlex's nouns

In [49]:
'''for item in hurtlex_AMI_pr[(hurtlex_AMI_pr.pos=='n')&(hurtlex_AMI_pr.level=='conservative')].lemma:
    offensive_women_noun.append(item)
offensive_women_noun'''

"for item in hurtlex_AMI_pr[(hurtlex_AMI_pr.pos=='n')&(hurtlex_AMI_pr.level=='conservative')].lemma:\n    offensive_women_noun.append(item)\noffensive_women_noun"

In [50]:
'''for item in hurtlex_AMI_dis[(hurtlex_AMI_dis.pos=='n')&(hurtlex_AMI_dis.level=='conservative')].lemma:
    offensive_generic.append(item)'''

"for item in hurtlex_AMI_dis[(hurtlex_AMI_dis.pos=='n')&(hurtlex_AMI_dis.level=='conservative')].lemma:\n    offensive_generic.append(item)"

In [51]:
editor.add_lexicon('women_noun', women_noun, overwrite=True)
editor.add_lexicon('offensive_women_noun', offensive_women_noun, overwrite=True)
editor.add_lexicon('offensive_homosexuals', offensive_homosexuals, overwrite=True)
editor.add_lexicon('work_role', work_role, overwrite=True)
editor.add_lexicon('fem_work_role', fem_work_role, overwrite=True)
editor.add_lexicon('male_work_role', male_work_role, overwrite=True)

_Adjectives_

In [52]:
print(', '.join(editor.suggest('She is {a:mask} {women_noun}.')[:100]))

amazing, extraordinary, old, incredible, older, excellent, exceptional, important, exemplary, American, outstanding, interesting, awesome, ordinary, unusual, ideal, great, honest, awful, beautiful, only, evil, lovely, emotional, odd, average, unbelievable, angry, Italian, unmarried, outspoken, elderly, elegant, admirable, good, inspiring, influential, honorable, elder, impressive, ambitious, wonderful, independent, active, enormous, eccentric, English, Indian, innocent, aging, Irish, unhappy, experienced, imposing, ancient, ugly, nice, understanding, African, artistic, unconventional, adventurous, young, strong, fantastic, happy, real, intelligent, terrific, accomplished, honorary, attractive, sweet, successful, educated, tough, actual, astonishing, absolute, uncommon, unexpected, inspirational, exquisite, remarkable, eminent, open, unfortunate, aggressive, alcoholic, imperfect, illustrious, absent, unforgettable, brilliant, unlikely, easy, astounding, invisible, iconic, single


In [53]:
print(', '.join(editor.suggest('She is {a:mask} {offensive_women_noun}.')[:100]))

fucking, evil, absolute, little, true, old, beautiful, ugly, actual, amazing, awful, excellent, incredible, arrogant, angry, enormous, utter, awesome, common, emotional, real, incompetent, abusive, insane, ignorant, American, adorable, obvious, idiot, wicked, ancient, good, great, total, attractive, pretty, adult, honest, complete, elderly, anonymous, bad, eternal, terrible, black, white, powerful, horrible, big, dead, nasty, dirty, perfect, young, damn, proud, annoying, strange, asshole, insecure, alcoholic, ultimate, extreme, immature, aggressive, animal, average, appalling, educated, older, easy, infamous, accomplished, adolescent, exquisite, odd, expert, Italian, Irish, innocent, intellectual, dangerous, active, vicious, aging, arch, anarchist, effective, female, master, original, mad, former, walking, lovely, dark, murderous, bloody, sex, blue


Some of the offensive adj are taken from:
* theodysseyonline.com/16-derogatory-words-used-to-describe-women

In [54]:
pos_adj = [                                                                             
    'adorable', 'amazing', 'astonishing', 'attractive', 'awesome', 'beautiful',
    'brilliant', 'caring', 'committed', 'cool', 'enthusiastic', 'excellent', 'exceptional',
    'extraordinary', 'fantastic', 'fun', 'good', 'great', 'happy', 'honest', 'impressive', 'incredible',
    'inspiring', 'intelligent', 'lovely', 'nice', 
    'successful', 'sweet', 'trustworthy', 'wise', 'wonderful']

neg_adj = [
    'absolute', 'aggressive', 'angry', 'annoying', 'arrogant', 
    'awful', 'bad', 'bitchy', 'bloody', 'boring', 'bossy', 'creepy', 'cruel', 
    'damn', 'dead', 'depressing', 'difficult', 'dirty', 'disappointing', 'disgusting', 
    'dreadful', 'emotional', 'evil', 'fake', 'fat', 'feisty', 'frustrating', 'fucking', 
    'giant', 'hormonal', 'horrible', 'hysterical', 'illogical', 'incompetent', 
    'irrational', 'irritating', 'lame', 'lousy', 'lying', 'nasty', 'poor', 
    'rough', 'sad', 'sassy', 'shameless', 'shitty', 'stupid', 'terrible', 'terrific', 
    'twatty', 'ugly', 'unhappy', 'wanky', 'weak', 'weird', 'whining', 'wicked', 'worst']

neutral_adj = [                                           
    'american', 'armenian','atheist', 'australian', 'black', 'british', 'christian', 'commercial', 
    'english', 'gay', 'immigrant', 'independent', 'independent', 'indian', 'indian', 'intellectual','busy', 
    'international', 'israeli', 'italian', 'jewish', 'married', 'muslim', 'old', 'poor',
    'private', 'rich', 'russian', 'single', 'tall', 'unmarried', 'white', 'working', 'young']

editor.add_lexicon('pos_adj', pos_adj, overwrite=True)
editor.add_lexicon('neg_adj', neg_adj, overwrite=True )
editor.add_lexicon('neutral_adj', neutral_adj, overwrite=True)

_Verbs_

In [55]:
print(', '.join(editor.suggest('I really {mask} {women_noun}.')[:100]))

like, miss, liked, love, mean, missed, hate, do, loved, am, appreciate, admire, respect, enjoy, did, enjoyed, dislike, want, wanted, feel, need, dig, was, care, believe, prefer, appreciated, think, have, felt, meant, know, hated, thought, see, hurt, admired, adore, needed, understand, value, got, disliked, trust, despise, thank, wish, hope, tried, fancy, the, heart, cherish, fell, married, lost, my, underestimated, blame, remember, envy, valued, resent, consider, fucking, get, a, sorry, helped, help, forgot, that, respected, cherished, say, call, had, support, called, understood, met, believed, preferred, are, likes, is, regret, trusted, wanna, missing, should, suck, worry, will, said, considered, try, liking, must, adopted


In [56]:
print(', '.join(editor.suggest('I really {mask} {offensive_women_noun}.')[:100]))

like, hate, liked, do, mean, dislike, love, am, did, miss, hated, enjoy, feel, want, was, despise, dig, prefer, enjoyed, fucking, wanted, appreciate, got, felt, disliked, think, need, wanna, get, a, meant, believe, loved, the, is, rather, missed, say, can, respect, resent, admire, understand, really, just, thought, fancy, suck, needed, know, preferred, have, hope, tried, blame, likes, go, LIKE, should, could, will, no, would, must, are, play, gotta, appreciated, adore, quite, bad, played, heart, said, don, lost, cannot, see, my, that, dont, read, trust, try, use, hurt, became, hit, dug, LOVE, fear, care, considered, smell, value, wish, fuck, regret, Like, never


In [57]:
pos_verb_present = ['like', 'enjoy', 'appreciate', 'love', 'admire',
                   'respect', 'adore', 'support', 'care for', 'fancy', 'treasure', 'trust']

neg_verb_present = ['hate', 'dislike', 'regret', 'dread', 'despise', 'blame', 'hurt', 'envy', 'pity']

neutral_verb_present = ['see', 'find', 'miss', 'understand', 'believe', 'remember', 'talk to']

pos_verb_past = ['liked', 'enjoyed', 'appreciated', 'loved', 'admired', 
                 'respected', 'adored', 'supported', 'cared for', 'treasured', 'trusted']

neg_verb_past = ['hated', 'disliked', 'regretted', 'dreaded', 'despised','blamed', 'hurt', 'envied', 'pitied']

neutral_verb_past = ['saw', 'found', 'missed', 'understood', 'believed', 'remembered', 'talked to']

editor.add_lexicon('pos_verb_present', pos_verb_present, overwrite=True)
editor.add_lexicon('neg_verb_present', neg_verb_present, overwrite=True)
editor.add_lexicon('neutral_verb_present', neutral_verb_present, overwrite=True)
editor.add_lexicon('pos_verb_past', pos_verb_past, overwrite=True)
editor.add_lexicon('neg_verb_past', neg_verb_past, overwrite=True)
editor.add_lexicon('neutral_verb_past', neutral_verb_past, overwrite=True)
editor.add_lexicon('pos_verb', pos_verb_present+ pos_verb_past, overwrite=True)
editor.add_lexicon('neg_verb', neg_verb_present + neg_verb_past, overwrite=True)
editor.add_lexicon('neutral_verb', neutral_verb_present + neutral_verb_past, overwrite=True)

_Intensifiers and reducers_

In [58]:
print(' , '.join(editor.suggest('{it} {be} {a:mask} {pos_adj} {women_noun}.', it=['She'], be=['is', 'was'])[:50]))

very , really , truly , extremely , absolutely , incredibly , most , pretty , quite , extraordinarily , amazingly , exceptionally , especially , exceedingly , enormously , unbelievably , immensely , equally , unusually , awfully , utterly , totally , rather , insanely , obviously , undeniably , altogether , overwhelmingly , overall , intensely , entirely , unexpectedly , amazing , absolute , almost , otherwise , extraordinary , seriously , overly , remarkably , incredible , endlessly , infinitely , always , ever , actually , outstanding , undoubtedly , real , enormous


In [59]:
print(' , '.join(editor.suggest('{it} {be} {a:mask} {neg_adj} {offensive_women_noun}.', it=['She'], be=['is', 'was'])[:50]))

very , really , fucking , pretty , absolutely , extremely , incredibly , especially , exceptionally , equally , utterly , exceedingly , extraordinarily , absolute , unbelievably , amazingly , rather , old , awfully , awful , insanely , obviously , ugly , evil , big , real , enormously , immensely , actual , enormous , even , undeniably , increasingly , obvious , inherently , almost , intensely , entirely , excellent , total , overall , amazing , incredible , admittedly , apparently , excessively , a , complete , extra , extraordinary


In [60]:
intens_adj = ['very', 'really', 'absolutely', 'truly', 'extremely', 'quite', 'incredibly', 'especially',
              'exceptionally', 'utterly', 'rather', 'totally', 'particularly',
              'remarkably', 'pretty', 'wonderfully', 'completely',
              'entirely', 'undeniably', 'highly']

editor.add_lexicon('intens_adj', intens_adj, overwrite=True)

In [61]:
print(', '.join(editor.suggest('{i} {mask} {pos_verb} {the} {women_noun}.', i=['I', 'We', 'You'], the=['this', 'that', 'the'])[:100]))

really, just, always, also, all, certainly, both, never, truly, definitely, actually, still, so, quite, absolutely, obviously, totally, genuinely, rather, greatly, clearly, thoroughly, probably, very, sure, simply, deeply, especially, already, even, seriously, particularly, completely, too, have, only, honestly, had, finally, kinda, desperately, much, almost, did, highly, were, mostly, generally, personally, strongly, immediately, do, guys, most, sincerely, fucking, instantly, REALLY, often, would, fully, dearly, surely, basically, hardly, are, secretly, ..., each, usually, ever, felt, must, should, immensely, apparently, literally, tremendously, first, sorely, pretty, we, somehow, badly, somewhat, more, might, two, feel, could, will, can, profoundly, now, ALL, initially, ultimately, naturally, better, barely


In [62]:
print(', '.join(editor.suggest('{i} {mask} {neg_verb} {the} {offensive_women_noun}.', i=['I', 'We', 'You'], the=['this', 'that', 'the'])[:100]))

really, always, just, also, still, truly, never, so, even, simply, only, absolutely, almost, actually, already, all, certainly, both, have, now, seriously, personally, must, greatly, probably, deeply, rather, fucking, definitely, finally, too, clearly, honestly, had, should, immediately, totally, especially, secretly, particularly, will, obviously, first, genuinely, sure, then, thoroughly, completely, sincerely, generally, much, usually, mostly, can, instantly, gotta, quite, often, forever, would, cannot, could, naturally, dearly, literally, very, might, badly, most, desperately, may, once, constantly, fully, better, do, somehow, long, shall, bitterly, ever, wanna, suddenly, rightly, surely, merely, instinctively, basically, people, nearly, severely, did, guys, two, gonna, strongly, kinda, utterly, openly, silently


In [63]:
intens_verb = ['really', 'absolutely', 'truly', 'extremely',  'especially',  'utterly',  'totally', 'particularly', 
               'highly', 'definitely', 'certainly', 'honestly', 'strongly', 'sincerely']
reducer_adj = ['somewhat', 'kinda', 'mostly', 'probably', 'generally', 'a little', 'a bit', 'slightly']

editor.add_lexicon('intens_verb', intens_verb, overwrite=True)
editor.add_lexicon('reducer_adj', reducer_adj, overwrite=True)

Original and new lexicons keys

In [64]:
print(list(editor.lexicons.keys()))

['male', 'female', 'first_name', 'first_pronoun', 'last_name', 'country', 'nationality', 'city', 'religion', 'religion_adj', 'sexual_adj', 'country_city', 'male_from', 'female_from', 'last_from', 'women_noun', 'offensive_women_noun', 'offensive_homosexuals', 'work_role', 'fem_work_role', 'male_work_role', 'pos_adj', 'neg_adj', 'neutral_adj', 'pos_verb_present', 'neg_verb_present', 'neutral_verb_present', 'pos_verb_past', 'neg_verb_past', 'neutral_verb_past', 'pos_verb', 'neg_verb', 'neutral_verb', 'intens_adj', 'intens_verb', 'reducer_adj']


## Capability 1: Vocabulary + POS

### Minimal Functionality Test

Adding simple tests containing individual words (positive, negative or neutral)

In [65]:
allow_for_neutral = lambda x, pred, _, label, _2 : pred != 0 if label == 1 else pred == label

In [66]:
# expectation: prediction is not 0
is_not_0 = lambda x, pred, *args: pred != 0

_Positive_

In [67]:
test = MFT(pos_adj + pos_verb_present + pos_verb_past, labels=2)
suite.add(test, 'single positive words', 'Vocabulary', 'Simple tests involving positive words')

In [68]:
test.data

['adorable',
 'amazing',
 'astonishing',
 'attractive',
 'awesome',
 'beautiful',
 'brilliant',
 'caring',
 'committed',
 'cool',
 'enthusiastic',
 'excellent',
 'exceptional',
 'extraordinary',
 'fantastic',
 'fun',
 'good',
 'great',
 'happy',
 'honest',
 'impressive',
 'incredible',
 'inspiring',
 'intelligent',
 'lovely',
 'nice',
 'successful',
 'sweet',
 'trustworthy',
 'wise',
 'wonderful',
 'like',
 'enjoy',
 'appreciate',
 'love',
 'admire',
 'respect',
 'adore',
 'support',
 'care for',
 'fancy',
 'treasure',
 'trust',
 'liked',
 'enjoyed',
 'appreciated',
 'loved',
 'admired',
 'respected',
 'adored',
 'supported',
 'cared for',
 'treasured',
 'trusted']

_Negative_

In [69]:
test = MFT(neg_adj + neg_verb_present + neg_verb_past, labels=0)
suite.add(test, 'single negative words', 'Vocabulary', 'Simple tests involving negative words')

In [70]:
test.data

['absolute',
 'aggressive',
 'angry',
 'annoying',
 'arrogant',
 'awful',
 'bad',
 'bitchy',
 'bloody',
 'boring',
 'bossy',
 'creepy',
 'cruel',
 'damn',
 'dead',
 'depressing',
 'difficult',
 'dirty',
 'disappointing',
 'disgusting',
 'dreadful',
 'emotional',
 'evil',
 'fake',
 'fat',
 'feisty',
 'frustrating',
 'fucking',
 'giant',
 'hormonal',
 'horrible',
 'hysterical',
 'illogical',
 'incompetent',
 'irrational',
 'irritating',
 'lame',
 'lousy',
 'lying',
 'nasty',
 'poor',
 'rough',
 'sad',
 'sassy',
 'shameless',
 'shitty',
 'stupid',
 'terrible',
 'terrific',
 'twatty',
 'ugly',
 'unhappy',
 'wanky',
 'weak',
 'weird',
 'whining',
 'wicked',
 'worst',
 'hate',
 'dislike',
 'regret',
 'dread',
 'despise',
 'blame',
 'hurt',
 'envy',
 'pity',
 'hated',
 'disliked',
 'regretted',
 'dreaded',
 'despised',
 'blamed',
 'hurt',
 'envied',
 'pitied']

_Neutral_

In [71]:
test = MFT(neutral_adj + neutral_verb_present + neutral_verb_past, labels=1)
suite.add(test, 'single neutral words', 'Vocabulary', 'Simple tests involving neutral words')

In [72]:
test.data

['american',
 'armenian',
 'atheist',
 'australian',
 'black',
 'british',
 'christian',
 'commercial',
 'english',
 'gay',
 'immigrant',
 'independent',
 'independent',
 'indian',
 'indian',
 'intellectual',
 'busy',
 'international',
 'israeli',
 'italian',
 'jewish',
 'married',
 'muslim',
 'old',
 'poor',
 'private',
 'rich',
 'russian',
 'single',
 'tall',
 'unmarried',
 'white',
 'working',
 'young',
 'see',
 'find',
 'miss',
 'understand',
 'believe',
 'remember',
 'talk to',
 'saw',
 'found',
 'missed',
 'understood',
 'believed',
 'remembered',
 'talked to']

Words in context: creating data-test from templates

_Positive and negative_

In [73]:
t = editor.template('{it} {women_noun} {be} {pos_adj}.', it=['The', 'That'], be=['is', 'was'], labels=2, nsamples=200, save=True)
t += editor.template('{it} {be} {a:pos_adj} {women_noun}.', it=['She'], be=['is', 'was'], labels=2, nsamples=200, save=True)
t += editor.template('{i} {pos_verb} {the} {women_noun}.', i=['I', 'We', 'You'], the=['this', 'that'], labels=2, nsamples=200, save=True)

t += editor.template('{it} {offensive_women_noun} {be} {neg_adj}.', it=['The', 'That'], be=['is', 'was'], labels=0, nsamples=200, save=True)
t += editor.template('{it} {be} {a:neg_adj} {offensive_women_noun}.', it=['She'], be=['is', 'was'], labels=0, nsamples=200, save=True)
t += editor.template('{i} {neg_verb} {the} {offensive_women_noun}.', i=['I', 'We', 'You'], the=['this', 'that'], labels=0, nsamples=200, save=True)

test = MFT(**t)
suite.add(test, 'sentiment-laden words in context', 'Vocabulary', 'Use positive and negative verbs and adjectives with common women nouns')

In [74]:
test.data

['The young lady is lovely.',
 'The sister was caring.',
 'That girlfriend is trustworthy.',
 'The girl is inspiring.',
 'The wife was wise.',
 'The mum was intelligent.',
 'The sister was caring.',
 'The partner is successful.',
 'That wife is sweet.',
 'That woman was trustworthy.',
 'That girl is enthusiastic.',
 'That girlfriend is exceptional.',
 'The daughter is great.',
 'The woman is caring.',
 'The wife is sweet.',
 'That girlfriend was caring.',
 'The daughter was trustworthy.',
 'That grandmother was honest.',
 'The grandmother was lovely.',
 'That partner was honest.',
 'The girlfriend is adorable.',
 'The mum is exceptional.',
 'The lady was wonderful.',
 'The girlfriend was brilliant.',
 'The girl is honest.',
 'The grandmother is adorable.',
 'That grandmother is wonderful.',
 'The wife is inspiring.',
 'The young lady was beautiful.',
 'The girlfriend is sweet.',
 'That girl is cool.',
 'The lady is inspiring.',
 'That mum was exceptional.',
 'That woman is impressive.'

_Neutral_

In [75]:
t = editor.template('{it} {women_noun} {be} {neutral_adj}.', it=['The', 'That'], be=['is', 'was'], labels=1,  nsamples=200, save=True)
t += editor.template('{it} {be} {a:neutral_adj} {women_noun}.', it=['She'], be=['is', 'was'], labels=1,  nsamples=200, save=True)
t += editor.template('{i} {neutral_verb} {the} {women_noun}.', i=['I', 'We', 'You'], the=['this', 'that'], labels=1,  nsamples=200, save=True)
test = MFT(t.data, Expect.single(is_not_0), templates=t.templates)
suite.add(test, 'neutral words in context', 'Vocabulary', 'Use neutral verbs and adjectives with common women nouns')

In [76]:
test.data

['The daughter is gay.',
 'The young lady is intellectual.',
 'That girlfriend was tall.',
 'The partner is married.',
 'That mum is independent.',
 'That girl is tall.',
 'That wife was private.',
 'The daughter was muslim.',
 'That wife is intellectual.',
 'The partner is muslim.',
 'The partner is russian.',
 'That young lady was atheist.',
 'That grandmother is australian.',
 'That sister is white.',
 'The mum was english.',
 'That wife is english.',
 'The girl is private.',
 'The girlfriend was busy.',
 'That woman is married.',
 'The sister was immigrant.',
 'The grandmother was working.',
 'The sister was christian.',
 'That sister is gay.',
 'The daughter is atheist.',
 'That mum is indian.',
 'That girl is young.',
 'The girl is australian.',
 'The wife was black.',
 'That mum was unmarried.',
 'The daughter was armenian.',
 'That mum was british.',
 'The lady is poor.',
 'The wife was immigrant.',
 'That partner was armenian.',
 'The wife was indian.',
 'That sister is christ

### Intensifiers and reducers

In [77]:
# We're  expecting the score to raise 
monotonic_label = Expect.monotonic(increasing=True, tolerance=0.1)
non_neutral_pred = lambda pred, *args, **kwargs: pred != 1
monotonic_label = Expect.slice_pairwise(monotonic_label, non_neutral_pred)

In [78]:
t = editor.template(['{it} {be} {a:pos_adj} {women_noun}.', '{it} {be} {a:intens} {pos_adj} {women_noun}.'] , intens=intens_adj, it=['She'], be=['is', 'was'], nsamples=200, labels=2, save=True)
t += editor.template(['{i} {pos_verb} {the} {women_noun}.', '{i} {intens} {pos_verb} {the} {women_noun}.'], intens=intens_verb, i=['I', 'We', 'You'], the=['this', 'that'], nsamples=200, labels=2, save=True)

t.data

[['She was an extraordinary young lady.',
  'She was an extremely extraordinary young lady.'],
 ['She was a wonderful young lady.',
  'She was an entirely wonderful young lady.'],
 ['She is a committed mum.', 'She is a remarkably committed mum.'],
 ['She was a fantastic sister.', 'She was a really fantastic sister.'],
 ['She is an adorable woman.', 'She is an utterly adorable woman.'],
 ['She is a lovely partner.', 'She is a wonderfully lovely partner.'],
 ['She was a caring sister.', 'She was an undeniably caring sister.'],
 ['She was an attractive sister.', 'She was an entirely attractive sister.'],
 ['She was an impressive wife.', 'She was a really impressive wife.'],
 ['She is a wise young lady.', 'She is a highly wise young lady.'],
 ['She was a fantastic grandmother.',
  'She was an exceptionally fantastic grandmother.'],
 ['She was a fun wife.', 'She was an undeniably fun wife.'],
 ['She is an exceptional lady.', 'She is a pretty exceptional lady.'],
 ['She is a committed grandm

In [79]:
test = DIR(t.data, monotonic_label, templates=t.templates)

description = '''Test is composed of pairs of sentences (x1, x2), where we add an intensifier
such as "really",or "very" to x2 and expect the confidence to NOT go down (with tolerance=0.1). e.g.:
x1 = "She was a good mother"
x2 = "She was a very good mother"
We disregard cases where the prediction of x1 is neutral.
'''

suite.add(test, 'intensifiers', 'Vocabulary', description)

In [80]:
# We're  expecting the score to fall 
monotonic_label_down = Expect.monotonic(increasing=False, tolerance=0.1)
monotonic_label_down = Expect.slice_pairwise(monotonic_label_down, non_neutral_pred)

In [81]:
t = editor.template(['{it} {be} {a:neg_adj} {offensive_women_noun}.', '{it} {be} {a:intens} {neg_adj} {offensive_women_noun}.'] , intens=intens_adj, it=['She'], be=['is', 'was'], nsamples=200, labels=0, save=True)
t += editor.template(['{i} {neg_verb} {the} {offensive_women_noun}.', '{i} {intens} {neg_verb} {the} {offensive_women_noun}.'], intens=intens_verb, i=['I', 'We', 'You'], the=['this', 'that'], nsamples=200, labels=0, save=True)

t += editor.template(['{it} {women_noun} {be} {pos_adj}.', '{it} {women_noun} {be} {red} {pos_adj}.'] , red=reducer_adj, it=['The', 'That'], be=['is', 'was'], nsamples=200, labels=2, save=True)
t += editor.template(['{it} {women_noun} {be} {neg_adj}.', '{it} {women_noun} {be} {red} {neg_adj}.'] , red=reducer_adj, it=['The', 'That'], be=['is', 'was'], nsamples=200, labels=0, save=True)
t.data

[['She is an arrogant ditsy.', 'She is a remarkably arrogant ditsy.'],
 ['She was a rough slut.', 'She was an extremely rough slut.'],
 ['She was a sassy bitch.', 'She was a highly sassy bitch.'],
 ['She was a hormonal bitch.', 'She was an utterly hormonal bitch.'],
 ['She is a worst whore.', 'She is a remarkably worst whore.'],
 ['She was an annoying spinster.', 'She was a wonderfully annoying spinster.'],
 ['She was a frustrating ditsy.', 'She was a pretty frustrating ditsy.'],
 ['She is a frustrating butch.', 'She is an undeniably frustrating butch.'],
 ['She is a boring slut.', 'She is an absolutely boring slut.'],
 ['She is an awful harpy.', 'She is a wonderfully awful harpy.'],
 ['She is a giant dyke.', 'She is a really giant dyke.'],
 ['She was a wicked slut.', 'She was a wonderfully wicked slut.'],
 ['She is an irrational skank.', 'She is a rather irrational skank.'],
 ['She is an irritating skank.', 'She is an absolutely irritating skank.'],
 ['She was a bad butch.', 'She was 

In [82]:
test = DIR(t.data, monotonic_label_down, templates=t.templates)

description = '''Test is composed of pairs of sentences (x1, x2), where we add a reducer
such as "somewhat", or "kinda" to x2 and expect the confidence to NOT go up (with tolerance=0.1). e.g.:
x1 = "The mum was good."
x2 = "The mum was somewhat good."
We disregard cases where the prediction of x1 is neutral.
'''

suite.add(test, 'reducers', 'Vocabulary', description)

### INVariance: change neutral words

In [83]:
neutral_words = set(
    ['.', 'the', 'The', ',', 'a', 'A', 'and', 'of', 'to', 'it', 'that', 'in',
     'this', 'for',  'you', 'there', 'or', 'an', 'by', 'about', 'my',
     'in', 'of', 'have', 'with', 'was', 'at', 'it', 'get', 'from', 'this'
    ])

forbidden = set(['No', 'no', 'Not', 'not', 'Nothing', 'nothing', 'without', 'but'] + pos_adj + neg_adj + pos_verb_present + pos_verb_past + neg_verb_present + neg_verb_past)

def change_neutral(d):
#     return d.text
    examples = []
    subs = []
    words_in = [x for x in d.capitalize().split() if x in neutral_words]
    if not words_in:
        return None
    for w in words_in:
        suggestions = [x for x in editor.suggest_replace(d, w, beam_size=5, words_and_sentences=True) if x[0] not in forbidden]
        examples.extend([x[1] for x in suggestions])
        subs.extend(['%s -> %s' % (w, x[0]) for x in suggestions])
    if examples:
        idxs = np.random.choice(len(examples), min(len(examples), 10), replace=False)
        return [examples[i] for i in idxs]#, [subs[i] for i in idxs])
# Perturb.perturb(parsed_data[:5], perturb)

In [84]:
t_pert = editor.template('{it} {women_noun} {be} {pos_adj}.', it=['The', 'That'], be=['is', 'was'], labels=2, nsamples=10, save=True)
t_pert += editor.template('{it} {be} {a:pos_adj} {women_noun}.', it=['She'], be=['is', 'was'], labels=2, nsamples=10, save=True)
t_pert += editor.template('{i} {pos_verb} {the} {women_noun}.', i=['I', 'We', 'You'], the=['this', 'that'], labels=2, nsamples=10, save=True)
t_pert += editor.template('{it} {offensive_women_noun} {be} {neg_adj}.', it=['The', 'That'], be=['is', 'was'], labels=0, nsamples=10, save=True)
t_pert += editor.template('{it} {be} {a:neg_adj} {offensive_women_noun}.', it=['She'], be=['is', 'was'], labels=0, nsamples=10, save=True)
t_pert += editor.template('{i} {neg_verb} {the} {offensive_women_noun}.', i=['I', 'We', 'You'], the=['this', 'that'], labels=0, nsamples=10, save=True)

In [85]:
t = Perturb.perturb(t_pert.data, change_neutral, nsamples=200) 

test = INV(t.data)

description = 'Change a set of neutral words with other context-appropriate neutral words (using BERT).'

suite.add(test, 'change neutral words with BERT', 'Vocabulary', description)

In [86]:
t.data

[['The woman was caring.',
  'A woman was caring.',
  'Each woman was caring.',
  'This woman was caring.',
  'One woman was caring.',
  'That woman was caring.',
  'Every woman was caring.',
  'The woman stopped caring.',
  'Another woman was caring.',
  'Neither woman was caring.',
  'The woman seemed caring.'],
 ['We appreciate that young lady.',
  'We appreciate our young lady.',
  'We appreciate this young lady.',
  'We appreciate her young lady.',
  'We appreciate them young lady.',
  'We appreciate a young lady.',
  'We appreciate these young lady.',
  'We appreciate to young lady.',
  'We appreciate hearing young lady.',
  'We appreciate you young lady.',
  'We appreciate everything young lady.'],
 ['She was a nice lady.', 'She is a nice lady.', 'She was very nice lady.'],
 ['You appreciated this daughter.',
  'You appreciated it daughter.',
  'You appreciated me daughter.',
  'You appreciated your daughter.',
  'You appreciated being daughter.',
  'You appreciated you daughter

### Add negative phrases

In [87]:
positive = editor.template('I {pos_verb_present} you.').data
positive += editor.template('Really {pos_adj}!').data
negative = editor.template('I {neg_verb_present} you.').data
negative += editor.template('Sooo {neg_adj}!').data

In [88]:
def add_phrase_function(phrases):
    def pert(d):
        while d[-1].pos_ == 'PUNCT':
            d = d[:-1]
        d = d.text
        ret = [d + '. ' + x for x in phrases]
        idx = np.random.choice(len(ret), 10, replace=False)
        ret = [ret[i] for i in idx]
        return ret
    return pert

def positive_change(orig_conf, conf):
    softmax = type(orig_conf) in [np.array, np.ndarray]
    if not softmax or orig_conf.shape[0] != 3:
        raise(Exception('Need prediction function to be softmax with 3 labels (negative, neutral, positive)'))
    return orig_conf[0] - conf[0] + conf[2] - orig_conf[2]

def diff_up(orig_pred, pred, orig_conf, conf, labels=None, meta=None):
    tolerance = 0.1
    change = positive_change(orig_conf, conf)
    if change + tolerance >= 0:
        return True
    else:
        return change + tolerance
    
def diff_down(orig_pred, pred, orig_conf, conf, labels=None, meta=None):
    tolerance = 0.1
    change = positive_change(orig_conf, conf)
    if change - tolerance <= 0:
        return True
    else:
        return -(change - tolerance)
    
goes_up = Expect.pairwise(diff_up)
goes_down = Expect.pairwise(diff_down)

In [89]:
t_parsed_data = list(nlp.pipe(t_pert.data))

In [90]:
t = Perturb.perturb(t_parsed_data, add_phrase_function(positive), nsamples=200)

test = DIR(t.data, goes_up)

description = 'Add very positive phrases (e.g. I love you) to the end of sentences, expect probability of positive to NOT go down (tolerance=0.1)'

suite.add(test, 'add positive phrases', 'Vocabulary', description)

In [91]:
t.data

[['We pity that skank.',
  'We pity that skank. Really amazing!',
  'We pity that skank. Really excellent!',
  'We pity that skank. Really adorable!',
  'We pity that skank. Really beautiful!',
  'We pity that skank. I enjoy you.',
  'We pity that skank. Really wonderful!',
  'We pity that skank. Really caring!',
  'We pity that skank. I fancy you.',
  'We pity that skank. Really attractive!',
  'We pity that skank. I support you.'],
 ['She is a damn dyke.',
  'She is a damn dyke. Really astonishing!',
  'She is a damn dyke. Really great!',
  'She is a damn dyke. Really honest!',
  'She is a damn dyke. Really extraordinary!',
  'She is a damn dyke. I love you.',
  'She is a damn dyke. Really lovely!',
  'She is a damn dyke. Really intelligent!',
  'She is a damn dyke. I adore you.',
  'She is a damn dyke. Really enthusiastic!',
  'She is a damn dyke. Really excellent!'],
 ['That frigid was dead.',
  'That frigid was dead. Really wonderful!',
  'That frigid was dead. Really enthusiastic

In [92]:
t = Perturb.perturb(t_parsed_data, add_phrase_function(negative), nsamples=200)

test = DIR(t.data, goes_down)

description = 'Add very negative phrases (e.g. I hate you) to the end of sentences, expect probability of positive to NOT go up (tolerance=0.1)'

suite.add(test, 'add negative phrases', 'Vocabulary', description)

In [93]:
t.data

[['The wife is wise.',
  'The wife is wise. Sooo terrific!',
  'The wife is wise. Sooo nasty!',
  'The wife is wise. Sooo wanky!',
  'The wife is wise. Sooo fat!',
  'The wife is wise. Sooo absolute!',
  'The wife is wise. Sooo feisty!',
  'The wife is wise. Sooo sad!',
  'The wife is wise. Sooo bossy!',
  'The wife is wise. Sooo irritating!',
  'The wife is wise. Sooo lousy!'],
 ['The lady is amazing.',
  'The lady is amazing. Sooo fat!',
  'The lady is amazing. Sooo bloody!',
  'The lady is amazing. Sooo terrible!',
  'The lady is amazing. Sooo giant!',
  'The lady is amazing. Sooo evil!',
  'The lady is amazing. Sooo bitchy!',
  'The lady is amazing. Sooo arrogant!',
  'The lady is amazing. Sooo irritating!',
  'The lady is amazing. Sooo hysterical!',
  'The lady is amazing. Sooo horrible!'],
 ['We like this mum.',
  'We like this mum. Sooo aggressive!',
  'We like this mum. Sooo dirty!',
  'We like this mum. Sooo giant!',
  'We like this mum. Sooo cruel!',
  'We like this mum. Sooo

## Capability 2: Robustness

To typos, irrelevant changes, etc

### INVariance: adding irrelevant linguistic segments before and after

In [94]:
import string
def random_string(n):
    return ''.join(np.random.choice([x for x in string.ascii_letters + string.digits], n))
def random_url(n=6):
    return 'https://t.co/%s' % random_string(n)
def random_handle(n=6):
    return '@%s' % random_string(n)

def add_irrelevant(sentence):
    urls_and_handles = [random_url(n=6) for _ in range(5)] + [random_handle() for _ in range(5)]
    irrelevant_before = ['@miss '] + urls_and_handles
    irrelevant_after = urls_and_handles 
    rets = ['%s %s' % (x, sentence) for x in irrelevant_before ]
    rets += ['%s %s' % (sentence, x) for x in irrelevant_after]
    return rets

In [95]:
t = Perturb.perturb(t_pert.data, add_irrelevant, nsamples=200)

test = INV(t.data)

suite.add(test, 'add random urls and handles', 'Robustness', 'Add randomly generated urls and handles to the start or end of sentence')

In [96]:
t.data

[['We adored this wife.',
  '@miss  We adored this wife.',
  'https://t.co/Gph53E We adored this wife.',
  'https://t.co/kMwvY4 We adored this wife.',
  'https://t.co/Is9svc We adored this wife.',
  'https://t.co/OSEeNB We adored this wife.',
  'https://t.co/EMLMsU We adored this wife.',
  '@DeLRS6 We adored this wife.',
  '@XnS1UU We adored this wife.',
  '@uMmkiO We adored this wife.',
  '@2ooaTy We adored this wife.',
  '@FAL8Gb We adored this wife.',
  'We adored this wife. https://t.co/Gph53E',
  'We adored this wife. https://t.co/kMwvY4',
  'We adored this wife. https://t.co/Is9svc',
  'We adored this wife. https://t.co/OSEeNB',
  'We adored this wife. https://t.co/EMLMsU',
  'We adored this wife. @DeLRS6',
  'We adored this wife. @XnS1UU',
  'We adored this wife. @uMmkiO',
  'We adored this wife. @2ooaTy',
  'We adored this wife. @FAL8Gb'],
 ['We hate this ditsy.',
  '@miss  We hate this ditsy.',
  'https://t.co/w2M5oW We hate this ditsy.',
  'https://t.co/ABsMyj We hate this di

### Punctuation, contractions, typos

In [97]:
t = Perturb.perturb(t_parsed_data, Perturb.punctuation, nsamples=200)

test = INV(t.data)

suite.add(test, 'punctuation', 'Robustness', 'Strip punctuation and / or add "."')

In [98]:
t.data

[['We care for this partner.', 'We care for this partner'],
 ['She is an incredible daughter.', 'She is an incredible daughter'],
 ['We adored this wife.', 'We adored this wife'],
 ['The girl is awesome.', 'The girl is awesome'],
 ['You respected this woman.', 'You respected this woman'],
 ['She is a great woman.', 'She is a great woman'],
 ['You adore this lady.', 'You adore this lady'],
 ['I blamed this hussy.', 'I blamed this hussy'],
 ['You hurt that hussy.', 'You hurt that hussy'],
 ['You regretted this cunt.', 'You regretted this cunt'],
 ['She was a cruel spinster.', 'She was a cruel spinster'],
 ['The woman was caring.', 'The woman was caring'],
 ['She is an adorable grandmother.', 'She is an adorable grandmother'],
 ['We hate this ditsy.', 'We hate this ditsy'],
 ['I appreciated that young lady.', 'I appreciated that young lady'],
 ['She is a beautiful young lady.', 'She is a beautiful young lady'],
 ['The daughter is attractive.', 'The daughter is attractive'],
 ['She was an 

In [99]:
t = Perturb.perturb(t_pert.data, Perturb.add_typos, nsamples=200, typos=1)

test = INV(t.data)

suite.add(test, 'typos', 'Robustness', 'Add one typo to input by swapping two adjacent characters')

In [100]:
t.data

[['She was a creepy spinster.', 'She was a creepy spisnter.'],
 ['I blamed this hussy.', 'I blamed tihs hussy.'],
 ['She was a sad wench.', 'She wsa a sad wench.'],
 ['That butch was depressing.', 'That butch was deperssing.'],
 ['The harpy was boring.', 'Theh arpy was boring.'],
 ['We like this mum.', 'eW like this mum.'],
 ['The harpy is dead.', 'Teh harpy is dead.'],
 ['That trollop was hysterical.', 'That trollop was hsyterical.'],
 ['You regretted this cunt.', 'You rgeretted this cunt.'],
 ['She was an ugly frigid.', 'She was an ugly frgiid.'],
 ['The wife is excellent.', 'Thew ife is excellent.'],
 ['That frigid was dead.', 'That frigid wasd ead.'],
 ['You adore this lady.', 'Yo uadore this lady.'],
 ['She was an astonishing woman.', 'She wsa an astonishing woman.'],
 ['She is a lousy dyke.', 'She is a losuy dyke.'],
 ['That young lady was incredible.', 'That young layd was incredible.'],
 ['The daughter is attractive.', 'The daughter is attractiev.'],
 ['The girl is awesome.', '

In [101]:
t = Perturb.perturb(t_pert.data, Perturb.add_typos, nsamples=200, typos=2)

test = INV(t.data)

suite.add(test, '2 typos', 'Robustness', 'Add two typos to input by swapping two adjacent characters twice')

In [102]:
t.data

[['The woman was caring.', 'Te hwoman was caring.'],
 ['That partner is extraordinary.', 'Taht partner is xetraordinary.'],
 ['We appreciate that young lady.', 'We appreicate thaty oung lady.'],
 ['You respected this woman.', 'You respecetd tihs woman.'],
 ['I appreciated that young lady.', 'I appreicated thaty oung lady.'],
 ['That hussy is irritating.', 'That hussy is irritatnig.'],
 ['I respect this sister.', 'I respect ths isister.'],
 ['That trollop was hysterical.', 'That trollop aw shysterical.'],
 ['She was an awesome girlfriend.', 'She was an awesoem girlfriedn.'],
 ['You regretted this cunt.', 'You regrettde this cutn.'],
 ['She is a happy woman.', 'She is a ahppyw oman.'],
 ['We pity that skank.', 'We pity that skank.'],
 ['The lady is amazing.', 'hTe lday is amazing.'],
 ['That frigid was dead.', 'Thtaf rigid was dead.'],
 ['That butch was depressing.', 'hTat butch wa sdepressing.'],
 ['That girlfriend is sweet.', 'That girlfriend is seewt.'],
 ['We blamed that hussy.', 'We

In [103]:
t = Perturb.perturb(t_pert.data, Perturb.contractions, nsamples=200)

test = INV(t.data)

suite.add(test, 'contractions', 'Robustness', 'Contract or expand contractions, e.g. What is -> What\'s')

In [104]:
t.data

[['She is an adorable grandmother.', "She's an adorable grandmother."],
 ['She is a beautiful young lady.', "She's a beautiful young lady."],
 ['She is a beautiful young lady.', "She's a beautiful young lady."],
 ['She is a worst cunt.', "She's a worst cunt."],
 ['She is a wicked ditsy.', "She's a wicked ditsy."],
 ['She is a difficult bitch.', "She's a difficult bitch."],
 ['She is a happy woman.', "She's a happy woman."],
 ['She is a lousy dyke.', "She's a lousy dyke."],
 ['She is a damn dyke.', "She's a damn dyke."],
 ['She is a great woman.', "She's a great woman."],
 ['She is an incredible daughter.', "She's an incredible daughter."]]

## Capability 3: NER

Appropriately understanding Named Entities

In [105]:
t = Perturb.perturb(parsed_data, Perturb.change_names, nsamples=200)

test = INV(t.data)

suite.add(test, 'change names', 'NER', 'Replace names with other common names')

In [106]:
t.data

[['My bitch a model, lil nigga, you could ask Tyra Banks That pussy wet like a bottle, change them sheets every day',
  'My bitch a model, lil nigga, you could ask Jennifer Cook That pussy wet like a bottle, change them sheets every day',
  'My bitch a model, lil nigga, you could ask Jessica Hernandez That pussy wet like a bottle, change them sheets every day',
  'My bitch a model, lil nigga, you could ask Ashley Gonzalez That pussy wet like a bottle, change them sheets every day',
  'My bitch a model, lil nigga, you could ask Sarah Edwards That pussy wet like a bottle, change them sheets every day',
  'My bitch a model, lil nigga, you could ask Emily Collins That pussy wet like a bottle, change them sheets every day',
  'My bitch a model, lil nigga, you could ask Amanda Gomez That pussy wet like a bottle, change them sheets every day',
  'My bitch a model, lil nigga, you could ask Elizabeth Nguyen That pussy wet like a bottle, change them sheets every day',
  'My bitch a model, lil ni

In [107]:
t = Perturb.perturb(parsed_data, Perturb.change_location, nsamples=200)

test = INV(t.data)

suite.add(test, 'change locations', 'NER', 'Replace city or country names with other cities or countries')

In [108]:
t.data

[["Tanzania Pardoned Two Child Rapists But Called For Arrest Of Pregnant Teens\nNews of the pedophile rapists' release emerged simultaneously as another government official called for pregnant pupils to be taken into custody. \n",
  "United Kingdom Pardoned Two Child Rapists But Called For Arrest Of Pregnant Teens\nNews of the pedophile rapists' release emerged simultaneously as another government official called for pregnant pupils to be taken into custody. \n",
  "Vietnam Pardoned Two Child Rapists But Called For Arrest Of Pregnant Teens\nNews of the pedophile rapists' release emerged simultaneously as another government official called for pregnant pupils to be taken into custody. \n",
  "Iran Pardoned Two Child Rapists But Called For Arrest Of Pregnant Teens\nNews of the pedophile rapists' release emerged simultaneously as another government official called for pregnant pupils to be taken into custody. \n",
  "China Pardoned Two Child Rapists But Called For Arrest Of Pregnant Teens

In [109]:
t = Perturb.perturb(parsed_data, Perturb.change_number, nsamples=200)

test = INV(t.data)

suite.add(test, 'change numbers', 'NER', 'Replace integers with random integers within a 20% radius of the original')

In [110]:
t.data

[["You would make more money if you had a boob-job. Then you'd be an 8 instead of a 6.",
  "You would make more money if you had a boob-job. Then you'd be an 9 instead of a 6.",
  "You would make more money if you had a boob-job. Then you'd be an 8 instead of a 7.",
  "You would make more money if you had a boob-job. Then you'd be an 7 instead of a 6.",
  "You would make more money if you had a boob-job. Then you'd be an 8 instead of a 4.",
  "You would make more money if you had a boob-job. Then you'd be an 6 instead of a 6.",
  "You would make more money if you had a boob-job. Then you'd be an 10 instead of a 6.",
  "You would make more money if you had a boob-job. Then you'd be an 10 instead of a 6.",
  "You would make more money if you had a boob-job. Then you'd be an 8 instead of a 5.",
  "You would make more money if you had a boob-job. Then you'd be an 6 instead of a 6.",
  "You would make more money if you had a boob-job. Then you'd be an 8 instead of a 5."],
 ['Women want ever

In [111]:
# expectation: prediction is not 0
is_not_0 = lambda x, pred, *args: pred != 0

In [112]:
t = editor.template('I met with {first_name} {last_name} last night.', nsamples=100, save=True)
test = MFT(t.data, Expect.single(is_not_0), templates=t.templates)
suite.add(test, 'change with English names', 'NER', 'Replace names with other common English names')

In [113]:
t.data[:5]

['I met with Jerry Williams last night.',
 'I met with Carl Richardson last night.',
 'I met with Louis Miller last night.',
 'I met with Florence Moore last night.',
 'I met with Sandra Martin last night.']

With foreign names:

In [114]:
first = [x.split()[0] for x in editor.lexicons.male_from.Germany +  editor.lexicons.female_from.Germany]
last = [x.split()[0] for x in editor.lexicons.last_from.Germany]
t = editor.template('I met with {first_name} {last_name} last night.', first_name=first, last_name=last, nsamples=100, save=True)
test = MFT(t.data, Expect.single(is_not_0), templates=t.templates)
suite.add(test, 'change with german names', 'NER', 'Replace names with other foreign names (german)')

In [115]:
t.data[:5]

['I met with Nicole Jung last night.',
 'I met with Irene Ludwig last night.',
 'I met with Beate Hartmann last night.',
 'I met with Brigitte Schäfer last night.',
 'I met with Marianne Hartmann last night.']

In [116]:
first = [x.split()[0] for x in editor.lexicons.male_from.Vietnam +  editor.lexicons.female_from.Vietnam]
last = [x.split()[0] for x in editor.lexicons.last_from.Vietnam]
t = editor.template('I met with {first_name} {last_name} last night.', first_name=first, last_name=last, nsamples=100, save=True)
test = MFT(t.data, Expect.single(is_not_0), templates=t.templates)
suite.add(test, 'change with vietnamese names', 'NER', 'Replace names with other foreign names (vietnamese)')

In [117]:
t.data[:5]

['I met with Alexandra Smith last night.',
 'I met with Michel Pham last night.',
 'I met with Minh Medina last night.',
 'I met with Mikhail Phong last night.',
 'I met with Charlie Đào last night.']

In [118]:
first = [x.split()[0] for x in editor.lexicons.male_from.Brazil +  editor.lexicons.female_from.Brazil]
last = [x.split()[0] for x in editor.lexicons.last_from.Brazil]
t = editor.template('I met with {first_name} {last_name} last night.', first_name=first, last_name=last, nsamples=100, save=True)
test = MFT(t.data, Expect.single(is_not_0), templates=t.templates)
suite.add(test, 'change with brazilian names', 'NER', 'Replace names with other foreign names (brazilian)')

In [119]:
t.data[:5]

['I met with Rita Motta last night.',
 'I met with João Alves last night.',
 'I met with Joana Freitas last night.',
 'I met with Maurício Rodrigues last night.',
 'I met with Flávio Maia last night.']

In [120]:
import re
def change_professions(x, *args, **kwargs):
    ret = []
    for p in work_role:
        if re.search(r'\b%s\b' % p, x):
            ret.extend([re.sub(r'\b%s\b' % p, p2, x) for p2 in work_role if p != p2])
    return ret

In [121]:
t = Perturb.perturb(sentences, change_professions, keep_original=True, nsamples=200)

test = INV(t.data)

suite.add(test, 'change profession', 'NER', 'Replace terms referring to work with different jobs')

In [122]:
t.data

[["Me:: I taught my kids today that some men can't handle when women are as smart or smarter than them. Male teacher:: Not anymore, right? Me:: Are you kidding? Him:: You really think still? After school, with students present (I am a woman teacher). Made me feel like nothing I teach my students will make people like him go the eff away.",
  "Me:: I taught my kids today that some men can't handle when women are as smart or smarter than them. Male astronaut:: Not anymore, right? Me:: Are you kidding? Him:: You really think still? After school, with students present (I am a woman astronaut). Made me feel like nothing I teach my students will make people like him go the eff away.",
  "Me:: I taught my kids today that some men can't handle when women are as smart or smarter than them. Male academic:: Not anymore, right? Me:: Are you kidding? Him:: You really think still? After school, with students present (I am a woman academic). Made me feel like nothing I teach my students will make peo

## Capability 4: Temporal Awareness

Understanding order of events

In [123]:
change = ['but', 'even though', 'although']
t = editor.template(['I used to think she was {neg_adj}, {change} now I think she is {pos_adj}.',
                                 'I think this girl is {pos_adj}, {change} I used to think she was {neg_adj}.',
                                 'In the past I thought that woman was {neg_adj}, {change} now I think she is {pos_adj}.',
                                 'I think she is {pos_adj}, {change} in the past I thought she was {neg_adj}.',
                                ] ,
                                 change=change, unroll=True, nsamples=500, save=True, labels=2)

t += editor.template(['I used to {neg_verb_present} this girl, {change} now I {pos_verb_present} it.',
                                 'I {pos_verb_present} this girl, {change} I used to {neg_verb_present} it.',
                                 'In the past I would {neg_verb_present} this girl, {change} now I {pos_verb} it.',
                                 'I {pos_verb_present} this girl, {change} in the past I would {neg_verb_present} it.',
                                ] ,
                                change=change, unroll=True, nsamples=500, save=True, labels=2)

t += editor.template(['I used to think this girl was {pos_adj}, {change} now I think she is {neg_adj}.',
                                 'I think this girl is {neg_adj}, {change} I used to think she was {pos_adj}.',
                                 'In the past I thought this girl was {pos_adj}, {change} now I think she is {neg_adj}.',
                                 'I think this girl is {neg_adj}, {change} in the past I thought she was {pos_adj}.',
                                ] ,
                                 change=change, unroll=True, nsamples=500, save=True, labels=0)

t += editor.template(['I used to {pos_verb_present} this girl, {change} now I {neg_verb_present} it.',
                                 'I {neg_verb_present} this girl, {change} I used to {pos_verb_present} it.',
                                 'In the past I would {pos_verb_present} this girl, {change} now I {neg_verb_present} it.',
                                 'I {neg_verb_present} this girl, {change} in the past I would {pos_verb_present} it.',
                                ] ,
                                change=change, unroll=True, nsamples=500, save=True, labels=0)

test = MFT(**t)

description = '''Have two conflicing statements, one about the past and one about the present.
Expect the present to carry the sentiment. Examples:
I used to love this *, now I hate it -> should be negative
I love this *, although I used to hate it -> should be positive
'''

suite.add(test, 'used to, but now', 'Temporal', description)

In [124]:
t.data

['I used to think she was nasty, but now I think she is astonishing.',
 'I think this girl is astonishing, but I used to think she was nasty.',
 'In the past I thought that woman was nasty, but now I think she is astonishing.',
 'I think she is astonishing, but in the past I thought she was nasty.',
 'I used to think she was irrational, although now I think she is good.',
 'I think this girl is good, although I used to think she was irrational.',
 'In the past I thought that woman was irrational, although now I think she is good.',
 'I think she is good, although in the past I thought she was irrational.',
 'I used to think she was hormonal, although now I think she is good.',
 'I think this girl is good, although I used to think she was hormonal.',
 'In the past I thought that woman was hormonal, although now I think she is good.',
 'I think she is good, although in the past I thought she was hormonal.',
 'I used to think she was nasty, but now I think she is sweet.',
 'I think this g

_Used to_ should reduce

In [125]:
t = editor.template(['She {be} {a:adj} {women_noun}.', 'I used to think she {be} {a:adj} {women_noun}.'], be=['is', 'was'], adj=editor.lexicons['pos_adj'] + editor.lexicons['neg_adj'], nsamples=250, save=True)
t += editor.template(['{i} {verb} {the} {women_noun}.', '{i} used to {verb} {the} {women_noun}.'], i=['I', 'We', 'You'], the=['this', 'that'], verb=editor.lexicons['pos_verb_present'] + editor.lexicons['neg_verb_present'], nsamples=250, save=True)

test = DIR(t.data, monotonic_label_down, templates=t.templates)

suite.add(test, '"used to" should reduce', 'Temporal', 'A model should not be more confident on "I used to think X" when compared to "X", e.g. "I used to love her" should have less confidence than "I love her"')

In [126]:
t.data

[['She is a sassy mum.', 'I used to think she is a sassy mum.'],
 ['She was a hysterical mum.', 'I used to think she was a hysterical mum.'],
 ['She is a wise mum.', 'I used to think she is a wise mum.'],
 ['She was an irrational lady.',
  'I used to think she was an irrational lady.'],
 ['She was an exceptional mum.',
  'I used to think she was an exceptional mum.'],
 ['She is a sassy woman.', 'I used to think she is a sassy woman.'],
 ['She is a weak lady.', 'I used to think she is a weak lady.'],
 ['She was a dreadful daughter.',
  'I used to think she was a dreadful daughter.'],
 ['She is a dreadful sister.', 'I used to think she is a dreadful sister.'],
 ['She is an emotional wife.', 'I used to think she is an emotional wife.'],
 ['She is an annoying daughter.',
  'I used to think she is an annoying daughter.'],
 ['She was a dead sister.', 'I used to think she was a dead sister.'],
 ['She is a wonderful daughter.',
  'I used to think she is a wonderful daughter.'],
 ['She was an a

_Before_ should reduce

In [127]:
t = editor.template(['She {be} {a:adj} {women_noun}.', 'Before I thought she {be} {a:adj} {women_noun}.'], be=['is', 'was'], adj=editor.lexicons['pos_adj'] + editor.lexicons['neg_adj'], nsamples=250, save=True)

test = DIR(t.data, monotonic_label_down, templates=t.templates)

suite.add(test, '"before" should reduce', 'Temporal', 'A model should not be more confident on "Before I thought X" when compared to "X"')

In [128]:
t.data

[['She is a honest girlfriend.',
  'Before I thought she is a honest girlfriend.'],
 ['She is an irrational girlfriend.',
  'Before I thought she is an irrational girlfriend.'],
 ['She is a wonderful sister.', 'Before I thought she is a wonderful sister.'],
 ['She was an extraordinary daughter.',
  'Before I thought she was an extraordinary daughter.'],
 ['She was a weak girl.', 'Before I thought she was a weak girl.'],
 ['She is an absolute lady.', 'Before I thought she is an absolute lady.'],
 ['She was a shitty sister.', 'Before I thought she was a shitty sister.'],
 ['She is an arrogant girl.', 'Before I thought she is an arrogant girl.'],
 ['She is a terrific partner.', 'Before I thought she is a terrific partner.'],
 ['She is a disgusting grandmother.',
  'Before I thought she is a disgusting grandmother.'],
 ['She is a shameless woman.', 'Before I thought she is a shameless woman.'],
 ['She is a twatty grandmother.',
  'Before I thought she is a twatty grandmother.'],
 ['She is 


## Capability 6: Negation

Simple templates: adding negations

In [129]:
t = editor.template('{it} {women_noun} {nt} {pos_adj}.', it=['This', 'That'], nt=['is not', 'isn\'t'], nsamples=200, save=True)
t += editor.template('{it} {benot} {a:pos_adj} {women_noun}.', it=['She'], benot=['is not',  'isn\'t', 'was not', 'wasn\'t'], nsamples=200, save=True)
neg = ['I can\'t say I', 'I don\'t', 'I would never say I', 'I don\'t think I', 'I didn\'t' ]
t += editor.template('{neg} {pos_verb_present} {the} {women_noun}.', neg=neg, the=['this', 'that'], nsamples=200, save=True)

t += editor.template('No one {pos_verb_present}s {the} {women_noun}.', neg=neg, the=['this', 'that'], nsamples=200, save=True)
t += editor.template('No one {pos_verb_present}s {the} {offensive_women_noun}.', neg=neg, the=['this', 'that'], nsamples=200, save=True)
t += editor.template('No one {pos_verb_present}s {a:offensive_homosexuals}.', neg=neg, nsamples=200, save=True)

test = MFT(t.data, labels=0, templates=t.templates)

suite.add(test, 'simple negations: negative', 'Negation', 'Very simple negations of positive statements')

In [130]:
t.data

["This sister isn't impressive.",
 'This mum is not astonishing.',
 'This wife is not brilliant.',
 'This girlfriend is not good.',
 'That daughter is not amazing.',
 'This girl is not good.',
 "This grandmother isn't inspiring.",
 "This grandmother isn't happy.",
 "This lady isn't intelligent.",
 "That girl isn't happy.",
 "That mum isn't exceptional.",
 "That mum isn't good.",
 'This daughter is not wise.',
 'That lady is not intelligent.',
 'That mum is not good.',
 "That lady isn't nice.",
 'This lady is not adorable.',
 "This woman isn't attractive.",
 "This daughter isn't brilliant.",
 "That lady isn't trustworthy.",
 "That girlfriend isn't good.",
 'That grandmother is not happy.',
 'That girlfriend is not amazing.',
 'This young lady is not trustworthy.',
 "That girl isn't exceptional.",
 "This mum isn't extraordinary.",
 "This mum isn't committed.",
 'This girl is not committed.',
 "This lady isn't impressive.",
 "This girlfriend isn't wise.",
 "This partner isn't happy.",
 "T

In [131]:
t = editor.template('{it} {women_noun} {nt} {neg_adj}.', it=['This', 'That'], nt=['is not', 'isn\'t'], nsamples=200, save=True)
t += editor.template('{it} {benot} {a:neg_adj} {women_noun}.', it=['She'], benot=['is not',  'isn\'t', 'was not', 'wasn\'t'], nsamples=200, save=True)
neg = ['I can\'t say I', 'I don\'t', 'I would never say I', 'I don\'t think I', 'I didn\'t' ]
t += editor.template('{neg} {neg_verb_present} {the} {women_noun}.', neg=neg, the=['this', 'that'], nsamples=200, save=True)
t += editor.template('No one {neg_verb_present}s {the} {women_noun}.', neg=neg, the=['this', 'that'], nsamples=200, save=True)

# expectation: prediction is not 0
is_not_0 = lambda x, pred, *args: pred != 0

test = MFT(t.data, Expect.single(is_not_0), templates=t.templates)

suite.add(test, 'simple negations: not negative', 'Negation', 'Very simple negations of negative statements. Expectation requires prediction to NOT be negative (i.e. neutral or positive)')

In [132]:
t.data

["That wife isn't cruel.",
 'That grandmother is not annoying.',
 "That girl isn't lying.",
 'That woman is not sassy.',
 "That partner isn't illogical.",
 "This mum isn't awful.",
 'That grandmother is not terrific.',
 "This girl isn't terrific.",
 'That partner is not damn.',
 'This young lady is not whining.',
 "That partner isn't emotional.",
 "This mum isn't sassy.",
 "That partner isn't creepy.",
 'That lady is not unhappy.',
 "This young lady isn't dreadful.",
 "That partner isn't creepy.",
 'That lady is not fucking.',
 "That partner isn't difficult.",
 "This lady isn't illogical.",
 "That woman isn't disgusting.",
 'This grandmother is not hormonal.',
 "This lady isn't ugly.",
 'That grandmother is not bad.',
 'This girl is not wanky.',
 "That girl isn't worst.",
 'This daughter is not unhappy.',
 'That grandmother is not hysterical.',
 "This girlfriend isn't boring.",
 "This wife isn't dreadful.",
 "This lady isn't arrogant.",
 "This grandmother isn't poor.",
 "This daughter 

In [133]:
t = editor.template('{it} {women_noun} {nt} {neutral_adj}.', it=['This', 'That'], nt=['is not', 'isn\'t'], nsamples=200, save=True)
t += editor.template('{it} {benot} {a:neutral_adj} {women_noun}.', it=['She'], benot=['is not',  'isn\'t', 'was not', 'wasn\'t'], nsamples=200, save=True)
neg = ['I can\'t say I', 'I don\'t', 'I would never say I', 'I don\'t think I', 'I didn\'t' ]
t += editor.template('{neg} {neutral_verb_present} {the} {women_noun}.', neg=neg, the=['this', 'that'], nsamples=200, save=True)

test = MFT(t.data, Expect.single(is_not_0), templates=t.templates)

suite.add(test, 'simple negations: not neutral is still neutral', 'Negation', 'Negating neutral statements should still result in neutral predictions')

In [134]:
t.data

["That wife isn't international.",
 'This wife is not italian.',
 "That young lady isn't black.",
 'This woman is not israeli.',
 "That mum isn't immigrant.",
 "That mum isn't working.",
 "That wife isn't immigrant.",
 'This girlfriend is not old.',
 'This wife is not private.',
 "This daughter isn't english.",
 "This girlfriend isn't rich.",
 'That mum is not rich.',
 'This sister is not indian.',
 "This partner isn't old.",
 'That mum is not commercial.',
 'That sister is not young.',
 "That grandmother isn't indian.",
 'That girlfriend is not single.',
 "This partner isn't indian.",
 "That sister isn't black.",
 "This daughter isn't english.",
 'This partner is not old.',
 'This sister is not single.',
 'This partner is not independent.',
 "That woman isn't british.",
 'This daughter is not armenian.',
 'That wife is not tall.',
 "That partner isn't british.",
 'This wife is not commercial.',
 'This partner is not married.',
 'That mum is not working.',
 'That daughter is not unmarr

Different templates:

In [135]:
t = editor.template('I thought {it} {women_noun} would be {pos_adj}, but it {neg}.', neg=['was not', 'wasn\'t'], it=['this', 'that'], nt=['is not', 'isn\'t'], nsamples=200, save=True)
t += editor.template('I thought I would {pos_verb_present} {the} {women_noun}, but I {neg}.', neg=['did not', 'didn\'t'], the=['this', 'that'], nsamples=200, save=True)

test = MFT(t.data, labels=0, templates=t.templates)

suite.add(test, 'simple negations (negative)', 'Negation', 'I thought x was positive, but it was not (should be negative)')

In [136]:
t.data

["I thought this girlfriend would be sweet, but it wasn't.",
 'I thought that daughter would be fantastic, but it was not.',
 'I thought that wife would be excellent, but it was not.',
 'I thought this wife would be attractive, but it was not.',
 'I thought this young lady would be happy, but it was not.',
 'I thought this young lady would be wise, but it was not.',
 "I thought this girlfriend would be awesome, but it wasn't.",
 'I thought this sister would be adorable, but it was not.',
 "I thought that partner would be intelligent, but it wasn't.",
 'I thought that sister would be adorable, but it was not.',
 'I thought this young lady would be astonishing, but it was not.',
 'I thought this wife would be excellent, but it was not.',
 "I thought that daughter would be honest, but it wasn't.",
 "I thought this mum would be lovely, but it wasn't.",
 'I thought this partner would be astonishing, but it was not.',
 "I thought that sister would be good, but it wasn't.",
 "I thought this g

In [137]:
t = editor.template('I thought {it} {women_noun} would be {neg_adj}, but it {neg}.', neg=['was not', 'wasn\'t'], it=['this', 'that'], nt=['is not', 'isn\'t'], nsamples=200, save=True)
t += editor.template('I thought I would {neg_verb_present} {the} {women_noun}, but I {neg}.', neg=['did not', 'didn\'t'], the=['this', 'that'], nsamples=200, save=True)

test = MFT(t.data, Expect.single(is_not_0), templates=t.templates)

suite.add(test, 'simple negations (neutral or positive)', 'Negation', 'I thought x was negative, but it was not (should be neutral or positive)')

In [138]:
t.data

["I thought this girlfriend would be hysterical, but it wasn't.",
 "I thought that sister would be unhappy, but it wasn't.",
 "I thought this daughter would be nasty, but it wasn't.",
 'I thought that young lady would be bloody, but it was not.',
 'I thought this grandmother would be terrible, but it was not.',
 "I thought that wife would be bitchy, but it wasn't.",
 'I thought this girl would be dreadful, but it was not.',
 "I thought that mum would be giant, but it wasn't.",
 'I thought this young lady would be sad, but it was not.',
 "I thought this woman would be fat, but it wasn't.",
 'I thought this mum would be creepy, but it was not.',
 'I thought that daughter would be poor, but it was not.',
 'I thought that wife would be hormonal, but it was not.',
 'I thought that young lady would be stupid, but it was not.',
 'I thought that sister would be fake, but it was not.',
 'I thought that girlfriend would be boring, but it was not.',
 'I thought this girl would be hormonal, but it

In [139]:
t = editor.template('I thought {it} {women_noun} would be {neutral_adj}, but it {neg}.', neg=['was not', 'wasn\'t'], it=['this', 'that'], nt=['is not', 'isn\'t'], nsamples=200, save=True)
t += editor.template('I thought I would {neutral_verb_present} {the} {women_noun}, but I {neg}.', neg=['did not', 'didn\'t'], the=['this', 'that'], nsamples=200, save=True)

test = MFT(t.data, Expect.single(is_not_0), templates=t.templates)

suite.add(test, 'simple negations (neutral)', 'Negation', 'I thought..., but it was not (neutral) should still be neutral')

In [140]:
t.data

['I thought that partner would be old, but it was not.',
 'I thought that girl would be commercial, but it was not.',
 'I thought that girlfriend would be married, but it was not.',
 'I thought that partner would be white, but it was not.',
 'I thought this wife would be busy, but it was not.',
 'I thought this young lady would be poor, but it was not.',
 'I thought that girlfriend would be married, but it was not.',
 'I thought that lady would be commercial, but it was not.',
 'I thought that lady would be atheist, but it was not.',
 "I thought this mum would be australian, but it wasn't.",
 'I thought that woman would be married, but it was not.',
 "I thought that girl would be gay, but it wasn't.",
 "I thought that sister would be rich, but it wasn't.",
 'I thought that mum would be poor, but it was not.',
 'I thought that girl would be tall, but it was not.',
 "I thought this woman would be married, but it wasn't.",
 "I thought this sister would be poor, but it wasn't.",
 'I though

Harder: negation with neutral in the middle

In [141]:
new_neg = neg[:-1]
neutral =['that I am from Brazil', 'my history with women', 'my history with men', 'the time that I\'ve been working'
          'the time that I\'ve been going', 'all that I\'ve seen over the years', 'it\'s a Tuesday',
          'it\'s late', 'it\'s early', 'the email that I\'ve received', 'the phone call that I\'ve had', 
          'my past relationships', 'my previous work', 'my former colleagues']
t = editor.template('{neg}, given {neutral}, that {it} {women_noun} {be} {pos_adj}.', neutral=neutral, neg=['I don\'t think', 'I can\'t say', 'I wouldn\'t say'], it=['this', 'that'], be=['is', 'was'], save=True)
t += editor.template('{neg}, given {neutral}, that {it} {be} {a:pos_adj} {women_noun}.',neutral=neutral,  neg=['I don\'t think', 'I can\'t say', 'I wouldn\'t say'], it=['this', 'that'], be=['is', 'was'], save=True)
t += editor.template('{neg}, given {neutral}, that {i} {pos_verb_present} {the} {women_noun}.',neutral=neutral,  neg=['I don\'t think', 'I can\'t say', 'I wouldn\'t say'], i=['I', 'we', 'you'], the=['this', 'that'], save=True)
t.data = list(np.random.choice(t.data, 1000, replace=False))

test = MFT(t.data, labels=0, templates=t.templates)

suite.add(test, 'hard negations: negative', 'Negation', 'Negation of positive with neutral stuff in the middle (should be negative)')

In [142]:
t.data

["I can't say, given it's early, that I support that girl.",
 "I wouldn't say, given all that I've seen over the years, that I adore this grandmother.",
 "I wouldn't say, given the time that I've been workingthe time that I've been going, that that is an awesome woman.",
 "I can't say, given it's late, that that girl is impressive.",
 "I wouldn't say, given it's late, that you treasure this lady.",
 "I wouldn't say, given it's a Tuesday, that I trust that young lady.",
 "I can't say, given my past relationships, that I appreciate this girlfriend.",
 "I wouldn't say, given my former colleagues, that that young lady was happy.",
 "I don't think, given my previous work, that I trust this wife.",
 "I can't say, given it's late, that this wife was awesome.",
 "I don't think, given my past relationships, that this is a good girl.",
 "I don't think, given all that I've seen over the years, that this young lady was good.",
 "I can't say, given it's a Tuesday, that that girlfriend is successful

In [143]:
t = editor.template('{neg}, given {neutral}, that {it} {women_noun} {be} {neg_adj}.', neutral=neutral, neg=['I don\'t think', 'I can\'t say', 'I wouldn\'t say'], it=['this', 'that'], be=['is', 'was'], save=True)
t += editor.template('{neg}, given {neutral}, that {it} {be} {a:neg_adj} {women_noun}.',neutral=neutral,  neg=['I don\'t think', 'I can\'t say', 'I wouldn\'t say'], it=['this', 'that'], be=['is', 'was'], save=True)
t += editor.template('{neg}, given {neutral}, that {i} {neg_verb_present} {the} {women_noun}.',neutral=neutral,  neg=['I don\'t think', 'I can\'t say', 'I wouldn\'t say'], i=['I', 'we', 'you'], the=['this', 'that'], save=True)
t.data = list(np.random.choice(t.data, 1000, replace=False))

test = MFT(t.data, Expect.single(is_not_0), templates=t.templates)

suite.add(test, 'hard negations: positive or neutral', 'Negation', 'Negation of negative with neutral stuff in the middle (should be positive or neutral)')

In [144]:
t.data

["I can't say, given it's a Tuesday, that I hate this grandmother.",
 "I don't think, given my former colleagues, that this was a disgusting partner.",
 "I can't say, given my history with women, that that is an illogical wife.",
 "I wouldn't say, given the phone call that I've had, that I dislike that grandmother.",
 "I can't say, given all that I've seen over the years, that that was a lying grandmother.",
 "I can't say, given my past relationships, that we envy that sister.",
 "I don't think, given it's a Tuesday, that this is a wanky lady.",
 "I wouldn't say, given it's late, that that is a wanky grandmother.",
 "I don't think, given my past relationships, that that partner was weird.",
 "I wouldn't say, given the phone call that I've had, that this was a terrific partner.",
 "I don't think, given it's early, that this daughter was wicked.",
 "I wouldn't say, given the email that I've received, that this is an arrogant daughter.",
 "I wouldn't say, given it's late, that that was a 

In [145]:
t = editor.template('{neg}, given {neutral}, that {it} {women_noun} {be} {neutral_adj}.', neutral=neutral, neg=['I don\'t think', 'I can\'t say', 'I wouldn\'t say'], it=['this', 'that'], be=['is', 'was'], save=True)
t += editor.template('{neg}, given {neutral}, that {it} {be} {a:neutral_adj} {women_noun}.',neutral=neutral,  neg=['I don\'t think', 'I can\'t say', 'I wouldn\'t say'], it=['this', 'that'], be=['is', 'was'], save=True)
t += editor.template('{neg}, given {neutral}, that {i} {neutral_verb_present} {the} {women_noun}.',neutral=neutral,  neg=['I don\'t think', 'I can\'t say', 'I wouldn\'t say'], i=['I', 'we', 'you'], the=['this', 'that'], save=True)
t.data = list(np.random.choice(t.data, 1000, replace=False))

test = MFT(t.data, Expect.single(is_not_0), templates=t.templates)

suite.add(test, 'negation of neutral', 'Negation', 'Negation of neutral with neutral in the middle, should still neutral')

In [146]:
t.data

["I don't think, given the email that I've received, that that was a christian partner.",
 "I can't say, given my previous work, that this grandmother was russian.",
 "I don't think, given my previous work, that this wife is tall.",
 "I can't say, given the phone call that I've had, that this sister is rich.",
 "I wouldn't say, given it's a Tuesday, that this woman was israeli.",
 "I don't think, given my history with women, that this young lady is christian.",
 "I can't say, given it's late, that this young lady is international.",
 "I can't say, given my past relationships, that that young lady was christian.",
 "I wouldn't say, given my history with men, that this was a single grandmother.",
 "I wouldn't say, given all that I've seen over the years, that that was an immigrant young lady.",
 "I can't say, given the time that I've been workingthe time that I've been going, that that is an international woman.",
 "I can't say, given my past relationships, that that grandmother was blac


## Capability 7: Semantic Role Labeling

Understanding roles such as agent, object, etc

My opinion is more important than others

In [147]:
# expectation: prediction is not 2
is_not_2 = lambda x, pred, *args: pred != 2

In [148]:
change = ['but', 'even though', 'although']
templates = ['Some people think you are {neg_adj}, {change} I think you are {pos_adj}.',
             'I think you are {pos_adj}, {change} some people think you are {neg_adj}.',
             'I had heard you were {neg_adj}, {change} I think you are {pos_adj}.',
             'I think you are {pos_adj}, {change} I had heard you were {neg_adj}.',
             ]
t = editor.template(templates, change=change, unroll=True, nsamples=200, save=True)

templates = ['{others} {neg_verb_present} you, {change} I {pos_verb_present} you.',
             'I {pos_verb_present} you, {change} {others} {neg_verb_present} you.',
            ]
others = ['some people', 'people', 'my parents', 'my friends']
t += editor.template(templates, others=others, change=change, unroll=True, nsamples=200, save=True)

test = MFT(t.data, Expect.single(is_not_0))

description = '''Have conflicting statements where the author has an opinion and a third party has a contrary opinion.
Expect sentiment to be the authors'. Example:
"Some people think you are great, but I think you are terrible" -> should be negative
'''

suite.add(test, 'my opinion is what matters, not negative', 'SRL', description)

In [149]:
t.data

['Some people think you are bloody, although I think you are good.',
 'I think you are good, although some people think you are bloody.',
 'I had heard you were bloody, although I think you are good.',
 'I think you are good, although I had heard you were bloody.',
 'Some people think you are shitty, although I think you are caring.',
 'I think you are caring, although some people think you are shitty.',
 'I had heard you were shitty, although I think you are caring.',
 'I think you are caring, although I had heard you were shitty.',
 'Some people think you are hormonal, but I think you are beautiful.',
 'I think you are beautiful, but some people think you are hormonal.',
 'I had heard you were hormonal, but I think you are beautiful.',
 'I think you are beautiful, but I had heard you were hormonal.',
 'Some people think you are awful, but I think you are awesome.',
 'I think you are awesome, but some people think you are awful.',
 'I had heard you were awful, but I think you are awes

In [150]:
templates = ['Some people think you are {pos_adj}, {change} I think you are {neg_adj}.',
             'I think you are {neg_adj}, {change} some people think you are {pos_adj}.',
             'I had heard you were {pos_adj}, {change} I think you are {neg_adj}.',
             'I think you are {neg_adj}, {change} I had heard you were {pos_adj}.',
             ]
t = editor.template(templates, change=change, unroll=True, nsamples=200, save=True)

templates = ['{others} {pos_verb_present} you, {change} I {neg_verb_present} you.',
             'I {neg_verb_present} you, {change} {others} {pos_verb_present} you.',
            ]
others = ['some people', 'my parents', 'my friends', 'people']
t += editor.template(templates, others=others, change=change, unroll=True, nsamples=200, save=True)

test = MFT(t.data, Expect.single(is_not_2))

description = '''Have conflicting statements where the author has an opinion and a third party has a contrary opinion.
Expect sentiment to be the authors'. Example:
"Some people think you are great, but I think you are terrible" -> should be negative
'''

suite.add(test, 'my opinion is what matters, not positive', 'SRL', description)

In [151]:
t.data

['Some people think you are honest, although I think you are shitty.',
 'I think you are shitty, although some people think you are honest.',
 'I had heard you were honest, although I think you are shitty.',
 'I think you are shitty, although I had heard you were honest.',
 'Some people think you are brilliant, although I think you are dead.',
 'I think you are dead, although some people think you are brilliant.',
 'I had heard you were brilliant, although I think you are dead.',
 'I think you are dead, although I had heard you were brilliant.',
 'Some people think you are incredible, but I think you are dirty.',
 'I think you are dirty, but some people think you are incredible.',
 'I had heard you were incredible, but I think you are dirty.',
 'I think you are dirty, but I had heard you were incredible.',
 'Some people think you are astonishing, although I think you are difficult.',
 'I think you are difficult, although some people think you are astonishing.',
 'I had heard you were a

Q & A form: yes

In [152]:
t = editor.template('Do I think {it} {women_noun} {be} {pos_adj}? Yes', it=['that', 'this'], be=['is', 'was'], nsamples=100, save=True)
t += editor.template('Do I think {it} {be} {a:pos_adj} {women_noun}? Yes', it=['she'], be=['is', 'was'], nsamples=100, save=True)
t += editor.template('Did {i} {pos_verb_present} {the} {women_noun}? Yes', i=['I', 'we', 'you'], the=['this', 'that'], nsamples=100, save=True)

test = MFT(t.data, Expect.single(is_not_0))

suite.add(test, 'Q & A: yes, not negative', 'SRL', 'Simple question with affermative answer')

In [153]:
t.data

['Do I think this woman is intelligent? Yes',
 'Do I think that grandmother is intelligent? Yes',
 'Do I think that grandmother was trustworthy? Yes',
 'Do I think that sister was inspiring? Yes',
 'Do I think this girlfriend was cool? Yes',
 'Do I think that mum is enthusiastic? Yes',
 'Do I think this sister was amazing? Yes',
 'Do I think this grandmother is excellent? Yes',
 'Do I think this young lady is exceptional? Yes',
 'Do I think this woman was astonishing? Yes',
 'Do I think this sister was lovely? Yes',
 'Do I think that mum is happy? Yes',
 'Do I think this girl was excellent? Yes',
 'Do I think this mum is fun? Yes',
 'Do I think that girlfriend was sweet? Yes',
 'Do I think this daughter was nice? Yes',
 'Do I think that girlfriend is enthusiastic? Yes',
 'Do I think this sister was trustworthy? Yes',
 'Do I think this girl was great? Yes',
 'Do I think that sister is honest? Yes',
 'Do I think this lady was caring? Yes',
 'Do I think that mum is exceptional? Yes',
 'Do

In [154]:
t = editor.template('Do I think {it} {offensive_women_noun} {be} {neg_adj}? Yes', it=['that', 'this'], be=['is', 'was'], nsamples=100, save=True)
t += editor.template('Do I think {it} {be} {a:neg_adj} {offensive_women_noun}? Yes', it=['she'], be=['is', 'was'], nsamples=100, save=True)
t += editor.template('Did {i} {neg_verb_present} {the} {offensive_women_noun}? Yes', i=['I', 'we', 'you'], the=['this', 'that'], nsamples=100, save=True)
t += editor.template('Did {i} {neg_verb_present} {offensive_homosexuals}? Yes', i=['I', 'we', 'you'], the=['this', 'that'], nsamples=100, save=True)

test = MFT(t.data, Expect.single(is_not_2))

suite.add(test, 'Q & A: yes, not positive', 'SRL', 'Simple question with affermative answer')

In [155]:
t.data

['Do I think this dyke is weird? Yes',
 'Do I think that slut is awful? Yes',
 'Do I think this skank was dirty? Yes',
 'Do I think that cunt was incompetent? Yes',
 'Do I think this bitch was fucking? Yes',
 'Do I think this bitch is terrific? Yes',
 'Do I think that dyke was angry? Yes',
 'Do I think that frigid is bitchy? Yes',
 'Do I think this harpy was disgusting? Yes',
 'Do I think this frigid is angry? Yes',
 'Do I think that slut is sad? Yes',
 'Do I think that witch is cruel? Yes',
 'Do I think this ditsy is difficult? Yes',
 'Do I think this skank was sad? Yes',
 'Do I think this harpy is bossy? Yes',
 'Do I think this spinster is nasty? Yes',
 'Do I think this dyke was lousy? Yes',
 'Do I think this frigid is absolute? Yes',
 'Do I think that wench is lousy? Yes',
 'Do I think that ditsy is hormonal? Yes',
 'Do I think that whore is sad? Yes',
 'Do I think this slut was emotional? Yes',
 'Do I think that cunt was rough? Yes',
 'Do I think that hussy was arrogant? Yes',
 'Do

In [156]:
t = editor.template('Do I think {it} {women_noun} {be} {neutral_adj}? Yes', it=['that', 'this'], be=['is', 'was'], nsamples=100, save=True)
t += editor.template('Do I think {it} {be} {a:neutral_adj} {women_noun}? Yes', it=['she'], be=['is', 'was'], nsamples=100, save=True)
t += editor.template('Did {i} {neutral_verb_present} {the} {women_noun}? Yes', i=['I', 'we', 'you'], the=['this', 'that'], nsamples=100, save=True)

test = MFT(t.data, Expect.single(is_not_0), templates=t.templates)

suite.add(test, 'Q & A: yes (neutral)', 'SRL', 'Simple question with affermative answer')

In [157]:
t.data

['Do I think this partner is italian? Yes',
 'Do I think that girlfriend was israeli? Yes',
 'Do I think this woman was armenian? Yes',
 'Do I think that mum is american? Yes',
 'Do I think this partner is international? Yes',
 'Do I think this daughter is young? Yes',
 'Do I think this woman is married? Yes',
 'Do I think that sister is poor? Yes',
 'Do I think that grandmother is indian? Yes',
 'Do I think that daughter is gay? Yes',
 'Do I think that lady was indian? Yes',
 'Do I think this wife is indian? Yes',
 'Do I think that woman was black? Yes',
 'Do I think that mum was commercial? Yes',
 'Do I think that mum was intellectual? Yes',
 'Do I think this daughter is jewish? Yes',
 'Do I think this young lady is independent? Yes',
 'Do I think that partner was international? Yes',
 'Do I think that woman was italian? Yes',
 'Do I think this daughter is italian? Yes',
 'Do I think that partner was christian? Yes',
 'Do I think this grandmother was private? Yes',
 'Do I think this 

Q & A form: no

In [158]:
allow_for_neutral = lambda x, pred, _, label, _2 : pred != 0 if label == 1 else pred == label

In [159]:
t = editor.template('Do I think {it} {women_noun} {be} {pos_adj}? No', it=['that', 'this'], be=['is', 'was'], nsamples=100, save=True)
t += editor.template('Do I think {it} {be} {a:pos_adj} {women_noun}? No', it=['she'], be=['is', 'was'], nsamples=100, save=True)
t += editor.template('Did {i} {pos_verb_present} {the} {women_noun}? No', i=['I', 'we', 'you'], the=['this', 'that'], nsamples=100, save=True)

test = MFT(t.data,  Expect.single(is_not_2), templates=t.templates)

suite.add(test, 'Q & A: no, not positive', 'SRL', 'Simple question with negative answer', overwrite=True)

In [160]:
t.data

['Do I think that young lady is attractive? No',
 'Do I think that woman was extraordinary? No',
 'Do I think that partner is exceptional? No',
 'Do I think that partner is committed? No',
 'Do I think this grandmother is lovely? No',
 'Do I think this girlfriend was sweet? No',
 'Do I think that grandmother is trustworthy? No',
 'Do I think this daughter was wise? No',
 'Do I think that partner was fun? No',
 'Do I think that girlfriend was amazing? No',
 'Do I think that girlfriend was impressive? No',
 'Do I think that sister is incredible? No',
 'Do I think this woman is successful? No',
 'Do I think that woman was inspiring? No',
 'Do I think this young lady was adorable? No',
 'Do I think this daughter is exceptional? No',
 'Do I think this woman was nice? No',
 'Do I think this partner is sweet? No',
 'Do I think that mum was wonderful? No',
 'Do I think that sister was sweet? No',
 'Do I think that daughter is adorable? No',
 'Do I think that girlfriend is incredible? No',
 'Do

In [161]:
t = editor.template('Do I think {it} {women_noun} {be} {neg_adj}? No', it=['that', 'this'], be=['is', 'was'], nsamples=100, save=True)
t += editor.template('Do I think {it} {be} {a:neg_adj} {women_noun}? No', it=['she'], be=['is', 'was'], nsamples=100, save=True)
t += editor.template('Did {i} {neg_verb_present} {the} {women_noun}? No', i=['I', 'we', 'you'], the=['this', 'that'], nsamples=100, save=True)

test = MFT(t.data,  Expect.single(is_not_0), templates=t.templates)

suite.add(test, 'Q & A: no, not negative', 'SRL', 'Simple question with negative answer', overwrite=True)

In [162]:
t.data

['Do I think this girlfriend was damn? No',
 'Do I think that girl is irritating? No',
 'Do I think that woman was dreadful? No',
 'Do I think that partner was ugly? No',
 'Do I think this daughter was angry? No',
 'Do I think this girl is weak? No',
 'Do I think that daughter is creepy? No',
 'Do I think that wife was shameless? No',
 'Do I think that sister is awful? No',
 'Do I think that woman was giant? No',
 'Do I think that daughter is illogical? No',
 'Do I think this wife was fucking? No',
 'Do I think that sister was wanky? No',
 'Do I think this mum was bloody? No',
 'Do I think that grandmother is wanky? No',
 'Do I think that mum is feisty? No',
 'Do I think this young lady is disappointing? No',
 'Do I think this young lady is bitchy? No',
 'Do I think that woman is bloody? No',
 'Do I think this young lady is frustrating? No',
 'Do I think this daughter was creepy? No',
 'Do I think that daughter is wanky? No',
 'Do I think that lady is sassy? No',
 'Do I think this daug

In [163]:
t = editor.template('Do I think {it} {women_noun} {be} {neutral_adj}? No', it=['that', 'this'], be=['is', 'was'], nsamples=100, save=True)
t += editor.template('Do I think {it} {be} {a:neutral_adj} {women_noun}? No', it=['she'], be=['is', 'was'], nsamples=100, save=True)
t += editor.template('Did {i} {neutral_verb_present} {the} {women_noun}? No', i=['I', 'we', 'you'], the=['this', 'that'], nsamples=100, save=True)

test = MFT(t.data,  Expect.single(is_not_0), templates=t.templates)

suite.add(test, 'Q & A: no (neutral)', 'SRL', 'Simple question with negative answer')

In [164]:
t.data

['Do I think this sister was independent? No',
 'Do I think this girl is gay? No',
 'Do I think that girl is busy? No',
 'Do I think this grandmother is international? No',
 'Do I think that lady is jewish? No',
 'Do I think that young lady is tall? No',
 'Do I think this daughter was immigrant? No',
 'Do I think this lady is unmarried? No',
 'Do I think that grandmother is black? No',
 'Do I think this girlfriend is independent? No',
 'Do I think that partner is busy? No',
 'Do I think that daughter was unmarried? No',
 'Do I think that woman was private? No',
 'Do I think that girl was married? No',
 'Do I think that wife is italian? No',
 'Do I think this woman is israeli? No',
 'Do I think this sister is italian? No',
 'Do I think that lady was immigrant? No',
 'Do I think this young lady was single? No',
 'Do I think this girl is independent? No',
 'Do I think this partner is immigrant? No',
 'Do I think that young lady was american? No',
 'Do I think this daughter is independent?

## Saving tests & Exporting the suite to a file

In [165]:
suite.to_raw_file('/Users/Marta/CheckList - FBK/1_AMI.txt', n=500, seed=1)

In [166]:
for test in suite.tests:
    suite.tests[test].name = test
    suite.tests[test].description = suite.info[test]['description]']
    suite.tests[test].capability = suite.info[test]['capability']

In [167]:
path = '/Users/Marta/opt/anaconda3/lib/python3.6/site-packages/checklist/release_data/sentiment/1_AMI.pkl'
suite.save(path)